# Sourcing Data

In [1]:
import matplotlib
import matplotlib.pyplot as plt

%matplotlib inline


In [2]:
savefig = input("save figures? ")
if "no" in savefig or "n" in savefig:
    savefig = False
    print(" ### NOT SAVING FIGURES ### ")
else:
    savefig = True
    print(" ### SAVING FIGURES ### ")

matplotlib.use("pgf")
matplotlib.rcParams.update({
    "pgf.texsystem": "pdflatex",
    'font.family': 'serif',
    'text.usetex': True,
    'pgf.rcfonts': False,
})

save figures? n
 ### NOT SAVING FIGURES ### 


In [3]:
import nasdaqdatalink
import os
import pandas as pd
nasdaqdatalink.ApiConfig.api_key = "6X-12CyLywuaJiyhmnzi"

## What data do we want? 

- Futures prices for a single commodity
- We want to get rolling price data, but the API will only give us data for a fixed month in a fixed year.
- Okay let's just try and get some data for say all the contracts in 2021.  

In [4]:
import logging

logging.basicConfig()

data_link_log = logging.getLogger('nasdaqdatalink')
data_link_log.setLevel(logging.DEBUG)

In [5]:
months = ['H', 'K', 'N', 'U', 'Z']

In [6]:
dataset = pd.DataFrame()
dataset = dataset.reindex(pd.date_range(start='1/1/2007', end='26/02/2022', freq='B'))
dataset = dataset.set_index(dataset.index.rename("Date"))
months_dict = dict({'H': "March", 'K': "May", 'N': "July", 'U': "September", 'Z': "December"})
column_names = []


for year in range(2010, 2025):
    for cct in months:
        label = 'SRF/CME_C{}'.format(cct + str(year))
        row = pd.DataFrame(nasdaqdatalink.get(label)["Settle"])
        column_names.append(cct+str(year))
        dataset = dataset.merge(row, on="Date", how="left")
        
dataset.columns = column_names

/Users/ubaidhoque/Projects/Dissertation/Code/env/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3340: UserWarning: Parsing '26/02/2022' in DD/MM/YYYY format. Provide format or specify infer_datetime_format=True for consistent parsing.
  exec(code_obj, self.user_global_ns, self.user_ns)
/var/folders/bn/nf5j5v796jjb6bncp9wnk5l80000gn/T/ipykernel_957/4172720896.py:13: FutureWarning: Passing 'suffixes' which cause duplicate columns {'Settle_x'} in the result is deprecated and will raise a MergeError in a future version.
  dataset = dataset.merge(row, on="Date", how="left")
/var/folders/bn/nf5j5v796jjb6bncp9wnk5l80000gn/T/ipykernel_957/4172720896.py:13: FutureWarning: Passing 'suffixes' which cause duplicate columns {'Settle_x'} in the result is deprecated and will raise a MergeError in a future version.
  dataset = dataset.merge(row, on="Date", how="left")
/var/folders/bn/nf5j5v796jjb6bncp9wnk5l80000gn/T/ipykernel_957/4172720896.py:13: FutureWarning: Passing 'suffixes' which 

/var/folders/bn/nf5j5v796jjb6bncp9wnk5l80000gn/T/ipykernel_957/4172720896.py:13: FutureWarning: Passing 'suffixes' which cause duplicate columns {'Settle_x'} in the result is deprecated and will raise a MergeError in a future version.
  dataset = dataset.merge(row, on="Date", how="left")
/var/folders/bn/nf5j5v796jjb6bncp9wnk5l80000gn/T/ipykernel_957/4172720896.py:13: FutureWarning: Passing 'suffixes' which cause duplicate columns {'Settle_x'} in the result is deprecated and will raise a MergeError in a future version.
  dataset = dataset.merge(row, on="Date", how="left")
/var/folders/bn/nf5j5v796jjb6bncp9wnk5l80000gn/T/ipykernel_957/4172720896.py:13: FutureWarning: Passing 'suffixes' which cause duplicate columns {'Settle_x'} in the result is deprecated and will raise a MergeError in a future version.
  dataset = dataset.merge(row, on="Date", how="left")
/var/folders/bn/nf5j5v796jjb6bncp9wnk5l80000gn/T/ipykernel_957/4172720896.py:13: FutureWarning: Passing 'suffixes' which cause duplic

In [7]:
from tabulate import tabulate
dataset.iloc[:, 18:23].plot()
plt.xlim('2010-01-01', '2015-01-01')
plt.ylabel("Price (\$)")
plt.title("Price CBOT Corn Futures contracts over time")
if savefig: plt.savefig('example.pgf')

In [8]:
dataset.iloc[500:600, :5]

H2010   K2010   N2010   U2010   Z2010
Date                                              
2008-12-01  409.75  417.25  423.25  418.25  413.25
2008-12-02  407.75  415.50  420.50  416.00  411.50
2008-12-03  407.00  414.25  419.25  424.00  409.25
2008-12-04  392.00  399.25  404.25  400.00  395.75
2008-12-05  364.00  371.50  378.25  374.50  370.00
...            ...     ...     ...     ...     ...
2009-04-13  431.25  438.75  445.75  442.25  438.25
2009-04-14  436.75  445.00  452.00  448.00  442.00
2009-04-15  427.25  435.25  442.25  438.25  432.25
2009-04-16  429.00  437.25  444.75  440.25  433.75
2009-04-17  419.50  426.25  432.50  428.50  422.50

[100 rows x 5 columns]

In [9]:
def roll(month):
    if month in {1,2,3}:
        return 0
    elif month in {4,5}:
        return 1
    elif month in {6,7}:
        return 2
    elif month in {8,9}:
        return 3
    elif month in {10,11,0}:
        return 4

def get_relative_future(contracts_ahead, fixed_dataset, current_date):
    day = current_date.day
    month = current_date.month
    if day >= 14 and month in {3,5,7,9,12}:
        return roll((month+1)%12) + contracts_ahead
    else:
        return roll(month%12) + contracts_ahead


In [10]:
from dateutil.relativedelta import relativedelta
rolling_dataset = pd.DataFrame()
rolling_dataset = rolling_dataset.reindex(pd.date_range(start='1/1/2010', end='26/02/2022', freq='B'))
rolling_dataset = rolling_dataset.set_index(rolling_dataset.index.rename("Date"))

rolling_prices = []
for i, date in enumerate(pd.date_range(start='1/1/2010', end='26/02/2022', freq='B')):
    cct = []
    for contracts_ahead in range(0, 10):
        years_added, contract_index = divmod(get_relative_future(contracts_ahead, dataset, date), 5)
        price = dataset[months[contract_index] + str((date + relativedelta(years=years_added)).year)][date]
        #price = dataset[get_relative_future(contracts_ahead, dataset, date) + str(date.year)][date]
        cct.append(price)
        #print(get_relative_future(contracts_ahead, dataset, date))
        #print(price)
    rolling_prices.append(cct)


/Users/ubaidhoque/Projects/Dissertation/Code/env/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3340: UserWarning: Parsing '26/02/2022' in DD/MM/YYYY format. Provide format or specify infer_datetime_format=True for consistent parsing.
  exec(code_obj, self.user_global_ns, self.user_ns)


In [11]:
rolling_dataset = pd.DataFrame(rolling_prices)

In [12]:
rolling_dataset = rolling_dataset.set_index(pd.date_range(start='1/1/2010', end='26/02/2022', freq='B'))

In [13]:
int_rolling_dataset = rolling_dataset.interpolate().pct_change()

# How can we generate time series data that would look like the commodity futures we have at the moment? 

The CBOT Corn futures are available for March (3)(H), May (5)(K), July (7)(N), Sep(9)(U), Dec (12)(Z) 

## Steps 

1. Construct a rolling dataset
    - It is possible to obtain a dataset or matrix with the rows as the dates and then the columns as the contracts. 
    - What we want to do is if say we want to look at 8 contracts into the future, then we want our dataset to have more than 8 columns, and then we want to use the date index to swap the columns when needed to get this rolling behaviour.
    - It is probably worth at this point to look at the different rolling mechanisms that are available.  May be more difficult to implement on the Macquarie side but at least we know that we've done the research part of it.  I think this is what we should do on the train back today.  

In [14]:
class RollingFutures(): 
    def init(self, start, end, asset, database, contracts):
        self.start = start
        self.end = end
        self.asset = asset
        self.database = database
        self.contracts = contracts

    def roll(month):
        if month in {1,2,3}:
            return 0
        elif month in {4,5}:
            return 1
        elif month in {6,7}:
            return 2
        elif month in {8,9}:
            return 3
        elif month in {10,11,12, 0}:
            return 4

    def get_relative_future(contracts_ahead, fixed_dataset, current_date):
        day = current_date.day
        month = current_date.month
        if day >= 14 and month in {3,5,7,9,12}:
            return months[(roll((month+1)%12) + contracts_ahead)%5]
        else:
            return months[(roll(month%12) + contracts_ahead)%5]

    def print_adf(data):

        from pandas import read_csv
        from statsmodels.tsa.stattools import adfuller
        X = data.dropna().values
        result = adfuller(X)
        print('ADF Statistic: %f' % result[0])
        print('p-value: %f' % result[1])
        print('Critical Values:')
        for key, value in result[4].items():
            print('\t%s: %.3f' % (key, value))

## We finally have data of an appropriate form to work with

In [15]:
# Let us first check for stationarity.

def calc_adf(data):
    from statsmodels.tsa.stattools import adfuller
    X = data.dropna().values
    result = adfuller(X)
    return result

def print_adf(result):

    print('ADF Statistic: %f' % result[0])
    print('p-value: %f' % result[1])
    print('Critical Values:')
    for key, value in result[4].items():
        print('\t%s: %.3f' % (key, value))

## Creating derived variables

In [16]:
import statistics
interpolated_rolling_dataset = rolling_dataset.interpolate()


# Volatility 
# Now we want to define some derived variables from the data that we have to feed into our HMM.

# LEVEL 
level = interpolated_rolling_dataset.mean(axis=1).dropna()


# We want the moving average over an x-day window

def mse_volatility(data):
    import numpy as np
    from sklearn.metrics import mean_squared_error as mse
    mean = data.mean()
    means = np.full((len(data)), mean)
    return mse(data, means)

volatility = level.rolling(10, min_periods=10).apply(statistics.stdev)

interpolated_rolling_dataset['level'] = level
interpolated_rolling_dataset['volatility'] = volatility

## Akaike Information Criterion (AIC) and Bayesian Information Criterion (BIC)

Note that we still need to figure out which rolling mechanism Macquarie use within the DataAG class. 

We want to use the AIC and BIC score to identify the optimal number of hidden states.  Of course, more states will lead to a higher score, but you want to add a penalty for that.  

In [17]:
# Volatility 

# We want the moving average over an x-day window
from statistics import stdev

def mse_volatility(data):
    import numpy as np
    from sklearn.metrics import mean_squared_error as mse
    mean = data.mean()
    means = np.full((len(data)), mean)
    return mse(data, means)/len(means)

volatility = level.rolling(10, min_periods=10).apply(mse_volatility)

In [18]:
interpolated_rolling_dataset.index.name = 'Date'

In [19]:
df = interpolated_rolling_dataset

In [20]:
from sklearn.decomposition import PCA
from sklearn.preprocessing import StandardScaler


In [21]:
from scipy import stats

In [22]:
from hmmlearn.hmm import GMMHMM
import numpy as np

def bic_general(likelihood_fn, k, X):
    """likelihood_fn: Function. Should take as input X and give out   the log likelihood
                  of the data under the fitted model.
           k - int. Number of parameters in the model. The parameter that we are trying to optimize.
                    For HMM it is number of states.
                    For GMM the number of components.
           X - array. Data that been fitted upon.
    """
    bic = np.log(len(X))*k - 2*likelihood_fn(X)
    return bic

def bic_general_hist(score, k, X):
    bic = np.log(len(X))*k - 2*score
    return bic

def bic_hmmlearn(X, min_states, max_states):
    lowest_bic = np.infty
    models=[]
    bic = []
    bic_history = []
    X = np.array(X).reshape(-1,1)
    n_states_range = range(min_states,max_states)
    for n_components in n_states_range:
        hmm_curr = GMMHMM(n_components=n_components, n_mix=2, covariance_type='full')
        hmm_curr.fit(X)
        models.append(hmm_curr)
        # Calculate number of free parameters
        # free_parameters = for_means + for_covars + for_transmat + for_startprob
        # for_means & for_covars = n_features*n_components
        n_features = hmm_curr.n_features
        n_mixtures = hmm_curr.weights_.shape[1]
        free_parameters = 2*(n_components*n_features*n_mixtures) + n_components*(n_components-1) + (n_components-1)

        # Firstly want the convergance of the BIC score to get a more detailed picture
        history_curr = list(hmm_curr.monitor_.history)
        bic_history_curr = map(lambda x: bic_general_hist(x, free_parameters, X), history_curr) 
        bic_history.append(bic_history_curr)
        
        bic_curr = bic_general(hmm_curr.score, free_parameters, X)
        bic.append(bic_curr)
        
        if bic_curr < lowest_bic:
            lowest_bic = bic_curr
        best_hmm = hmm_curr
    return (best_hmm, bic, bic_history, models)



In [23]:
from hmmlearn.hmm import GMMHMM
import numpy as np

def aic_general(likelihood_fn, k, X):
    """likelihood_fn: Function. Should take as input X and give out   the log likelihood
                  of the data under the fitted model.
           k - int. Number of parameters in the model. The parameter that we are trying to optimize.
                    For HMM it is number of states.
                    For GMM the number of components.
           X - array. Data that been fitted upon.
    """
    aic = 2*k - 2*likelihood_fn(X)
    return aic

def aic_general_hist(score, k, X):
    aic = 2*k - 2*score
    return aic

def aic_hmmlearn(X, min_states, max_states):
    lowest_aic = np.infty
    models=[]
    aic = []
    aic_history = []
    X = np.array(X).reshape(-1,1)
    n_states_range = range(min_states,max_states)
    for n_components in n_states_range:
        hmm_curr = GMMHMM(n_components=n_components,n_mix=2, covariance_type='full')
        hmm_curr.fit(X)
        models.append(hmm_curr)
        # Calculate number of free parameters
        # free_parameters = for_means + for_covars + for_transmat + for_startprob
        # for_means & for_covars = n_features*n_components
        n_features = hmm_curr.n_features
        n_mixtures = hmm_curr.weights_.shape[1]
        free_parameters = 2*(n_components*n_features*n_mixtures) + n_components*(n_components-1) + (n_components-1)

        # Firstly want the convergance of the BIC score to get a more detailed picture
        history_curr = list(hmm_curr.monitor_.history)
        aic_history_curr = map(lambda x: aic_general_hist(x, free_parameters, X), history_curr) 
        aic_history.append(aic_history_curr)
        
        aic_curr = aic_general(hmm_curr.score, free_parameters, X)
        aic.append(aic_curr)
        
        if aic_curr < lowest_aic:
            lowest_aic = aic_curr
        best_hmm = hmm_curr
    return (best_hmm, aic, aic_history, models)



# Identifying Regimes

The problem that Faheem identified, what ramifications could it actually have? 

If we don't have the same number of each contract, then this could affect our final calculation as those contracts will be weighted more? 

This step is fine but we need to first manually identify what the best number of states to use is.  

# KMO and Barlett Test

In [24]:
"""
Created on Sat Sep 10 20:21:04 2016
Bartlett Sphericity Test Function:
- This test evaluates sampling adequacy for exploratory Factor Analysis
Bartlett_Sphericity function has two inputs:
- The Dataset (numerical or ordinal variables only)
- The correlation method (spearman or pearson)
It Outputs the test result, degrees of freedom and p-value
@authors: Rui Sarmento
          Vera Costa
"""

#Bartlett Sphericity Test
#Exploratory factor analysis is only useful if the matrix of population 
#correlation is statistically different from the identity matrix. 
#If these are equal, the variables are few interrelated, i.e., the specific 
#factors explain the greater proportion of the variance and the common factors
#are unimportant. Therefore, it should be defined when the correlations 
#between the original variables are sufficiently high. 
#Thus, the factor analysis is useful in estimation of common factors. 
#With this in mind, the Bartlett Sphericity test can be used. The hypotheses are:

# H0: the matrix of population correlations is equal to the identity matrix
# H1: the matrix of population correlations is different from the identity matrix.

def bartlett_sphericity(dataset, corr_method="pearson"):
    
    r"""
    
    Parameters
    ----------
    dataset : dataframe, mandatory (numerical or ordinal variables)
        
    corr_method : {'pearson', 'spearman'}, optional
        
    Returns
    -------
    out : namedtuple
        The function outputs the test value (chi2), the degrees of freedom (ddl)
        and the p-value.
        It also delivers the n_p_ratio if the number of instances (n) divided 
        by the numbers of variables (p) is more than 5. A warning might be issued.
        
        Ex:
        chi2:  410.27280642443156
        ddl:  45.0
        p-value:  8.73359410503e-61
        n_p_ratio:    20.00
        
        Out: Bartlett_Sphericity_Test_Results(chi2=410.27280642443156, ddl=45.0, pvalue=8.7335941050291506e-61)
    
    References
    ----------
    
    [1] Bartlett,  M.  S.,  (1951),  The  Effect  of  Standardization  on  a  chi  square  Approximation  in  Factor
    Analysis, Biometrika, 38, 337-344.
    [2] R. Sarmento and V. Costa, (2017)
    "Comparative Approaches to Using R and Python for Statistical Data Analysis", IGI-Global.
    
    Examples
    --------
    illustration how to use the function.
    
    >>> bartlett_sphericity(survey_data, corr_method="spearman")
    chi2:  410.27280642443145
    ddl:  45.0
    p-value:  8.73359410503e-61
    n_p_ratio:    20.00
    C:\Users\Rui Sarmento\Anaconda3\lib\site-packages\spyderlib\widgets\externalshell\start_ipython_kernel.py:75: 
    UserWarning: NOTE: we advise  to  use  this  test  only  if  the number of instances (n) divided by the number of variables (p) is lower than 5. Please try the KMO test, for example.
    backend_o = CONF.get('ipython_console', 'pylab/backend', 0)
    Out[12]: Bartlett_Sphericity_Test_Results(chi2=410.27280642443156, ddl=45.0, pvalue=8.7335941050291506e-61)
    """
    
    import numpy as np
    import math as math
    import scipy.stats as stats
    import warnings as warnings
    import collections

    #Dimensions of the Dataset
    n = dataset.shape[0]
    p = dataset.shape[1]
    n_p_ratio = n / p
    
    #Several Calculations
    chi2 = - (n - 1 - (2 * p + 5) / 6) * math.log(np.linalg.det(dataset.corr(method=corr_method)))
    #Freedom Degree
    ddl = p * (p - 1) / 2
    #p-value
    pvalue = 1 - stats.chi2.cdf(chi2 , ddl)
    
    Result = collections.namedtuple("Bartlett_Sphericity_Test_Results", ["chi2", "ddl", "pvalue"], verbose=False, rename=False)   
    
    #Output of the results - named tuple
    result = Result(chi2=chi2,ddl=ddl,pvalue=pvalue) 

    
    #Output of the function
    if n_p_ratio > 5 :
        print("n_p_ratio: {0:8.2f}".format(n_p_ratio))
        warnings.warn("NOTE: we advise  to  use  this  test  only  if  the number of instances (n) divided by the number of variables (p) is lower than 5. Please try the KMO test, for example.")
        
    
    return result
    

"""
Created on Sat Sep 10 20:21:04 2016
KMO Test Function:
- This test evaluates sampling adequacy for exploratory Factor Analysis
KMO Test function has one input:
- The Dataset Correlation Matrix
It Outputs the test result, and the results per variable
@authors: Rui Sarmento
          Vera Costa
"""

#KMO Test
#KMO is a measure of the adequacy of sampling “Kaiser-Meyer-Olkin" and checks 
#if it is possible to factorize the main variables efficiently.
#The correlation matrix is always the starting point. The variables are more or
#less correlated, but the others can influence the correlation between the two 
#variables. Hence, with KMO, the partial correlation is used to measure the 
#relation between two variables by removing the effect of the remaining variables.

def kmo(dataset_corr):
    
    import numpy as np
    import math as math
    import collections
    
    r"""
    
    Parameters
    ----------
    dataset_corr : ndarray
        Array containing dataset correlation
        
    Returns
    -------
    out : namedtuple
        The function outputs the test value (value), the test value per variable (per_variable)
       
        Ex:
        Out[30]: 
        KMO_Test_Results(value=0.798844102413, 
        per_variable=
        Q1     0.812160468405
        Q2     0.774161264483
        Q3     0.786819432663
        Q4     0.766251123086
        Q5     0.800579196084
        Q6     0.842927745203 
        Q7     0.792010173432 
        Q8     0.862037322891
        Q9     0.714795031915 
        Q10    0.856497242574
        dtype: float64)
    
    References
    ----------    
    [1] Kaiser, H. F. (1970). A second generation little jiffy. Psychometrika, 35(4), 401-415.
    [2] Kaiser, H. F. (1974). An index of factorial simplicity. Psychometrika, 39(1), 31-36.
    [3] R. Sarmento and V. Costa, (2017)
    "Comparative Approaches to Using R and Python for Statistical Data Analysis", IGI-Global
    
    Examples
    --------
    illustration how to use the function.
    
    >>> kmo_test(survey_data.corr(method="spearman"))
         
        KMO_Test_Results(value=0.798844102413, 
        per_variable=
        Q1     0.812160468405
        Q2     0.774161264483
        Q3     0.786819432663
        Q4     0.766251123086
        Q5     0.800579196084
        Q6     0.842927745203 
        Q7     0.792010173432 
        Q8     0.862037322891
        Q9     0.714795031915 
        Q10    0.856497242574
        dtype: float64) 
"""
    
    

    #KMO Test
    #inverse of the correlation matrix
    corr_inv = np.linalg.inv(dataset_corr)
    nrow_inv_corr, ncol_inv_corr = dataset_corr.shape
    
    #partial correlation matrix
    A = np.ones((nrow_inv_corr,ncol_inv_corr))
    for i in range(0,nrow_inv_corr,1):
        for j in range(i,ncol_inv_corr,1):
            #above the diagonal
            A[i,j] = - (corr_inv[i,j]) / (math.sqrt(corr_inv[i,i] * corr_inv[j,j]))
            #below the diagonal
            A[j,i] = A[i,j]
    
    #transform to an array of arrays ("matrix" with Python)
    dataset_corr = np.asarray(dataset_corr)
        
    #KMO value
    kmo_num = np.sum(np.square(dataset_corr)) - np.sum(np.square(np.diagonal(dataset_corr)))
    kmo_denom = kmo_num + np.sum(np.square(A)) - np.sum(np.square(np.diagonal(A)))
    kmo_value = kmo_num / kmo_denom
    
    
    kmo_j = [None]*dataset_corr.shape[1]
    #KMO per variable (diagonal of the spss anti-image matrix)
    for j in range(0, dataset_corr.shape[1]):
        kmo_j_num = np.sum(dataset_corr[:,[j]] ** 2) - dataset_corr[j,j] ** 2
        kmo_j_denom = kmo_j_num + np.sum(A[:,[j]] ** 2) - A[j,j] ** 2
        kmo_j[j] = kmo_j_num / kmo_j_denom

    
    Result = collections.namedtuple("KMO_Test_Results", ["value", "per_variable"])   
    
    #Output of the results - named tuple    
    return Result(value=kmo_value,per_variable=kmo_j)

# Building Strategy

In [25]:
class Portfolio():
    def __init__(self, capital):
        self.orders = []
        self.capital_hist = []
        self.capital = capital
        self.starting_capital = capital
        self.total_value = []
        self.reason = []
 
    def __repr__(self):
        long = []
        short = []
        for order in self.orders:
            if order['type'] == 'BUY':
                long.append(order)
            else:
                short.append(order)
#         print('LONG:\n')
#         print(long)
#         print('SHORT:\n')
#         print(short)

        
    def __add_position__(self, order_type: str, future: int, contracts: int, price: float):
        order = {
            'type': order_type,
            'future': future,
            'order_type': order_type,
            'contracts': contracts,
            'price': price,
        }
                    
        self.orders.append(order)
        

    def __liquidate__(self, curr_day: int, price_df):
        '''
        Close out all positions in porfolio and add profits
        '''
        date = price_df.index[curr_day]
        portfolio_profit = 0
        proceeds_from_longs = 0
        money_on_shorts = 0
        for order in self.orders:
            future = order['future']
            contracts = order['contracts']
            order_type = order['order_type']
            price = price_df.loc[date, future]
           
            if order_type == "BUY":
                proceeds_from_longs += contracts*price
#                 print("FUTURE {0} sold at {1} for {2} contracts".format(future, price, contracts))
            else:
                money_on_shorts += contracts*price
#                 print("FUTURE {0} bought at {1} for {2} contracts".format(future, price, contracts))
        
            earned = contracts * price
            portfolio_profit += earned
 

#         print("PROCEEDS FROM LONGS: {}".format(proceeds_from_longs))
#         print("MONEY ON SHORTS: {}".format(money_on_shorts))
        print("NET MONEY FROM LIQUIDATION: {}".format(portfolio_profit))
#         print('CAPITAL BEFORE: {}'.format(self.capital))
        self.capital_hist.append([date, portfolio_profit])
        self.capital += portfolio_profit
#         print('CAPITAL AFTER: {}'.format(self.capital))
            
        # Clear orders 
        self.orders = []
        
    def __get_contracts_value__(self, curr_day: int, price_df):
        date = price_df.index[curr_day]
        portfolio_profit = 0
        proceeds_from_longs = 0
        money_on_shorts = 0
        for order in self.orders:
            future = order['future']
            contracts = order['contracts']
            order_type = order['order_type']
            price = price_df.loc[date, future]
           
            if order_type == "BUY":
                proceeds_from_longs += contracts*price
            else:
                money_on_shorts += contracts*price
            
            earned = contracts * price
            portfolio_profit += earned
 
        return portfolio_profit
        
    def __is_empty__(self):
        if not self.orders:
            return True
        else: 
            return False
        



In [26]:
class PCA_Strategy():
    
    def __init__(self, df, roll_day, capital, expanding: bool):
        self.df = df
        self.roll_day = roll_day
        self.expanding = expanding
        self.portfolio = Portfolio(capital)
        self.trading_df = df
                                                           
    def __set_train_df__(self, curr_day: int, wdw_length):
        
        from datetime import timedelta
        
        assert curr_day - wdw_length > -1, 'window outside of range'
        
        self.curr_day = curr_day
        self.wdw_length = wdw_length
    
        end_date = self.df.index[curr_day]
        start_date = self.df.index[curr_day - wdw_length]
        if self.expanding:
            self.train_df = self.df.loc[:end_date].iloc[:,:10].copy()
        else:
            self.train_df = self.df.loc[start_date:end_date].iloc[:,:10].copy()

    def __pca__(self, X, n_components):
        
        from sklearn.decomposition import PCA
        from sklearn.preprocessing import StandardScaler
        import numpy as np
        
        #print(kmo(X.dropna().corr()))
        
        idx = X.index
        pca = PCA(n_components)
        X_scaled = StandardScaler().fit_transform(X)
        pca.fit(X_scaled)
        scores = pca.transform(X_scaled)
        loadings = pca.components_
        reconstructed_data = pd.DataFrame(np.dot(scores, loadings)).set_index(idx)
        residuals = pd.DataFrame(StandardScaler().fit_transform(self.train_df)).set_index(idx) - reconstructed_data
        eig_vals = pca.explained_variance_
        
        self.scores = scores
        self.loadings = loadings
        self.reconstructed_data = reconstructed_data
        self.eig_vals = eig_vals
        self.residuals = residuals
            
    def __get_residuals__(self, date_idx: int):
        
        date = self.df.index[date_idx]
        
        return self.residuals.loc[date, :]
    
    def __remove_nontrading_days__(self, holding_period, contract_months: list):
        
        from datetime import datetime, timedelta
        import pandas as pd
        
        self.holding_period = holding_period
        trading_df = self.df.copy()
        start_year = self.train_df.index[0].year
        end_year = self.train_df.index[-1].year
        
        for yr in range(start_year, end_year + 1):
            for cm in contract_months:
                roll_date = datetime(yr, cm, self.roll_day)
                
                # If Saturday or Sunday return Friday
                wkday = roll_date.weekday()
                if wkday > 4:
                    roll_date = roll_date + timedelta(-1 * (wkday - 4))
                
                for day in pd.date_range(roll_date + timedelta(-1 * holding_period), roll_date):
                    if day in trading_df.index:
                        trading_df.drop(day, inplace=True)
                        
        self.trading_df = trading_df
    
    
    def __add_total_value__(self, curr_day):
        date = self.df.index[curr_day]
        portfolio_value = self.portfolio.__get_contracts_value__(curr_day, self.df)
        total_val = portfolio_value + self.portfolio.capital
        self.portfolio.total_value.append(total_val)
#         print("Total Value: {}".format(total_val))
        
    def __run__(self, holding_period, first_trading_day_idx, wdw_length): 
        import numpy as np
        import math
        import statistics
        
        # Build HMM and remove non trading days
        
        self.__set_train_df__(first_trading_day_idx, wdw_length)
        self.__remove_nontrading_days__(holding_period, [3,5,7,9,12])
        self.trading_df = self.df.copy()
        self.curr_holding_period = holding_period

        while self.curr_day < len(self.df) - 1 and self.portfolio.capital > 0:
            
#             print("--------------------------")
            print("\nCurrent Day: " + str(self.df.index[self.curr_day]))
            print(holding_period)
            print(wdw_length)
#             print("\nPortfolio: ")
#             print(self.portfolio.__repr__())
#             print("\nCapital: {}".format(self.portfolio.capital))
#             print("--------------------------")
            
            self.__set_train_df__(self.curr_day, self.wdw_length)
            level = self.train_df.mean(axis=1).dropna()
            volatility = level.rolling(10, min_periods=10).apply(mse_volatility)
            strat_df = self.train_df.copy()
            strat_df['level'] = level
            strat_df['volatility'] = volatility
            
            X = np.array(obs1).reshape(-1, 1)
            self.__pca__(self.train_df.fillna(self.train_df.mean()), 3)
            
            self.__remove_nontrading_days__(holding_period, [3,5,7,9,12])
            date = self.df.index[self.curr_day]
            self.__add_total_value__(self.curr_day)
            
            if self.portfolio.__is_empty__():   
                # Trading day?
                if date in self.trading_df.index:
                    # Buy
                    residuals = self.__get_residuals__(self.curr_day)
                    residuals_std = self.residuals.std()
                    residuals_sum = abs(residuals).sum()
                    non_zero_residuals = residuals[residuals != 0]
                
                    c_is = []
                    daily_spend = 0
                    min_c_i = math.inf
                    
                    for i, residual in enumerate(residuals):
                        if abs(residual) > 0.1*residuals_std[i]:
                            price = self.df.loc[date, i]
                            c_i = abs(residual)/price
                            c_is.append([c_i, i, price, np.sign(residual)])
                            if c_i < min_c_i:
                                min_c_i = c_i

                    factor = 1/min_c_i
                    for c_i, i, price, sign in c_is:
                        # if res is positive want to short
                        contracts = round(-1 * sign * c_i * factor)                    
                        if sign < 0:
                            order_type = 'BUY'
                        else:
                            order_type = 'SELL'

                        self.portfolio.__add_position__(order_type, i, contracts, price)
                        self.portfolio.capital = self.portfolio.capital - contracts*price
                    
#                     print("DAILY SPEND: {}".format(daily_spend))
            
            ## Selling
            
            else:
                if self.curr_holding_period < 1:
                    self.portfolio.reason.append([date, 'Holding Period'])
                    self.portfolio.__liquidate__(self.curr_day, self.df)
                    self.curr_holding_period = self.holding_period
#                     print("###########HOLDING PERIOD EXPIRED#############")
                else:
                    self.curr_holding_period = self.curr_holding_period - 1
                    
            self.curr_day = self.curr_day + 1
                
            

In [27]:
class PCA_HMM_Strategy():
    
    def __init__(self, df, n_components, roll_day, capital, expanding:bool):
        self.df = df
        self.n_components = n_components
        self.roll_day = roll_day
        self.expanding = expanding
        self.portfolio = Portfolio(capital)
                                                       
    def __set_train_df__(self, curr_day: int, wdw_length):
        
        from datetime import timedelta
        
        assert curr_day - wdw_length > -1, 'window outside of range'
        
        self.curr_day = curr_day
        self.wdw_length = wdw_length
    
        end_date = self.df.index[curr_day]
        start_date = self.df.index[curr_day - wdw_length]
        if self.expanding:
            self.train_df = self.df.loc[:end_date].iloc[:,:10].copy()
        else:
            self.train_df = self.df.loc[start_date:end_date].iloc[:,:10].copy()
        
        
    def __identify_regimes__(self, X, covariance_type):
        
        import hmmlearn as hmm
        
        model = GMMHMM(n_components=self.n_components, n_mix=2, covariance_type=covariance_type)
        model.fit(X)
        self.train_df['hidden_states'] = model.decode(X)[1]
        
    def __get_state_df__(self, component):
        return self.train_df[self.train_df.hidden_states == component]

    def __pca__(self, X, n_components):
        
        from sklearn.decomposition import PCA
        from sklearn.preprocessing import StandardScaler
        import numpy as np
        
        #print(kmo(X.dropna().corr()))
        
        idx = X.index
        pca = PCA(n_components)
        X_scaled = StandardScaler().fit_transform(X)
        pca.fit(X_scaled)
        scores = pca.transform(X_scaled)
        loadings = pca.components_
        reconstructed_data = pd.DataFrame(np.dot(scores, loadings)).set_index(idx)
        eig_vals = pca.explained_variance_
        
        return scores, loadings, reconstructed_data, eig_vals

    def __regime_pca__(self, n_components):
        from sklearn.preprocessing import StandardScaler
        pcs = dict()
        for hs in self.train_df['hidden_states'].unique():
            hs_df = self.__get_state_df__(hs).iloc[:, :-1]
            hs_df = hs_df.fillna(hs_df.mean())
            idx = hs_df.index
            scores, loadings, reconstructed_data, eig_vals = self.__pca__(hs_df, 3)
            residuals = pd.DataFrame(StandardScaler().fit_transform(hs_df)).set_index(idx) - reconstructed_data
            pcs[hs] = {'scores': scores,
                      'loadings': loadings,
                       'reconstructed_data': reconstructed_data,
                       'eig_vals': eig_vals,
                       'residuals': residuals
                      }
        self.pcs = pcs
            
    def __get_residuals__(self, date_idx: int, regime: int):
        
        date = self.df.index[date_idx]
        
        return self.pcs[regime]['residuals'].loc[date, :]
    
    def __get_regime__(self, date_idx:int):
        
        date = self.df.index[date_idx]
        
        return self.train_df.loc[date, 'hidden_states']
    
    def __remove_nontrading_days__(self, holding_period, contract_months: list):
        
        from datetime import datetime, timedelta
        import pandas as pd
        
        self.holding_period = holding_period
        trading_df = self.df.copy()
        start_year = self.train_df.index[0].year
        end_year = self.train_df.index[-1].year
        
        for yr in range(start_year, end_year + 1):
            for cm in contract_months:
                roll_date = datetime(yr, cm, self.roll_day)
                
                # If Saturday or Sunday return Friday
                wkday = roll_date.weekday()
                if wkday > 4:
                    roll_date = roll_date + timedelta(-1 * (wkday - 4))
                
                for day in pd.date_range(roll_date + timedelta(-1 * holding_period), roll_date):
                    if day in trading_df.index:
                        trading_df.drop(day, inplace=True)
                        
        self.trading_df = trading_df
                
    def __add_total_value__(self, curr_day):
        date = self.df.index[curr_day]
        portfolio_value = self.portfolio.__get_contracts_value__(curr_day, self.df)
        total_val = portfolio_value + self.portfolio.capital
        self.portfolio.total_value.append(total_val)
#         print("Total Value: {}".format(total_val))
    
    def __run__(self, holding_period, first_trading_day_idx, wdw_length): 
        import numpy as np
        import math
        
        self.__set_train_df__(first_trading_day_idx, wdw_length)
        #self.__remove_nontrading_days__(holding_period, [3,5,7,9,12])
        self.trading_df = self.df.copy()
        self.curr_holding_period = holding_period
        self.holding_period = holding_period

        while self.curr_day < len(self.df) - 1 and self.portfolio.capital > 0:
             
#             print("--------------------------")
            print("\nCurrent Day: " + str(self.df.index[self.curr_day]))
            print(holding_period)
            print(wdw_length)
#             print("\nPortfolio: ")
#             print(self.portfolio.__repr__())
#             print("\nCapital: {}".format(self.portfolio.capital))
            self.__add_total_value__(self.curr_day)
#             print("\nHolding Period: {}".format(self.holding_period))
#             print("\nWindow Length: {}".format(wdw_length))
#             print("--------------------------")
            
            date = self.df.index[self.curr_day]
            
            self.__set_train_df__(self.curr_day, self.wdw_length)
            level = self.train_df.mean(axis=1).dropna()
            volatility = level.rolling(10, min_periods=10).apply(stdev)
            
            strat_df = self.train_df.copy()
            strat_df['level'] = level
            strat_df['volatility'] = volatility
        
            obs1 = strat_df['level'].pct_change().bfill()
            obs2 = strat_df['volatility'].diff().fillna(df['volatility'].diff().mean())
            
            X = np.array(obs1).reshape(-1, 1)
            
            self.__identify_regimes__(X, 'full')
            self.__regime_pca__(self.n_components)
            
            
            if self.portfolio.__is_empty__():   
                # Trading day?
                    # Buy
                    residuals = self.__get_residuals__(self.curr_day, self.__get_regime__(self.curr_day))
                    residuals_std = self.pcs[self.__get_regime__(self.curr_day)]['residuals'].std()
                    residuals_sum = abs(residuals).sum()
                    non_zero_residuals = residuals[residuals != 0]
                
                    c_is = []
                    daily_spend = 0
                    min_c_i = math.inf
                    
                    for i, residual in enumerate(residuals):
                        if abs(residual) > 0.1*residuals_std[i]:
                            price = self.df.loc[date, i]
                            c_i = abs(residual)/price
                            c_is.append([c_i, i, price, np.sign(residual)])
                            if c_i < min_c_i:
                                min_c_i = c_i

                    factor = 1/min_c_i
                    for c_i, i, price, sign in c_is:
                        # if res is positive want to short
                        contracts = round(-1 * sign * c_i * factor)                    
                        if sign < 0:
                            order_type = 'BUY'
                        else:
                            order_type = 'SELL'

                        self.portfolio.__add_position__(order_type, i, contracts, price)
                        self.portfolio.capital = self.portfolio.capital - contracts*price
                    
#                     print("DAILY SPEND: {}".format(daily_spend))
                    self.portfolio.capital_hist.append([date, self.portfolio.capital])
 
            ## Selling
            
            else:
                
                # Sell if regime has changed or held for holding period
                curr_regime = self.__get_regime__(self.curr_day)
                prev_regime = self.__get_regime__(self.curr_day - 1)
                
                if curr_regime != prev_regime:
                    self.portfolio.reason.append([date, 'Regime Change'])
                    self.portfolio.__liquidate__(self.curr_day, self.df)
                    self.curr_holding_period = self.holding_period
#                     print("###########REGIME CHANGED################")
                elif self.curr_holding_period < 1:
                    self.portfolio.reason.append([date, 'Holding Period'])
                    self.portfolio.__liquidate__(self.curr_day, self.df)
                    self.curr_holding_period = self.holding_period
#                     print("###########HOLDING PERIOD EXPIRED#############")
                else:  
                    self.curr_holding_period = self.curr_holding_period - 1
                    
            self.curr_day = self.curr_day + 1

            # Buying

            
                            
#                     for i, residual in enumerate(residuals):
                      
#                         contracts = round(abs(residual)*100/abs(residuals).sum())
#                         price = self.df.loc[date, :][i]
                        
#                         ## if residuals bigger than two standard deviations, only then act
#                         if abs(residual) > 2*residuals_std[i]:
#                             if residual < 0:
#                                 order_type = 'BUY'
#                             else:
#                                 order_type = 'SELL'
                            
#                             self.portfolio.__add_position__(order_type, i, contracts, price)
                    


Contracts roll over on the 14th of the month of the contract unless this is not a business day and markets are closed, in this case contracts roll over either on the 13th of the 12th.

Want to go through contracts from first month to last month

# How to weight strategies?



In [28]:
from sklearn.model_selection import train_test_split
final_train_df, final_test_df = train_test_split(df.copy(), test_size=0.4, shuffle=False)

In [29]:
obs1 = final_train_df['level'].pct_change().bfill()
obs2 = final_train_df['volatility'].diff().fillna(df['volatility'].diff().mean())
#X = [[x[0], x[1]] for x in zip(obs1, obs2)]
X = obs1 

In [30]:
final_train_df['obs1'] = obs1
final_train_df['obs2'] = obs2

In [71]:
benchmark_strategies_exp = dict()
for holding_period in [3, 5, 10, 15]:
    strategy = PCA_Strategy(final_train_df, 15, 100000, True)
    strategy.__run__(holding_period, 252, 252)
    if not strategy.portfolio.__is_empty__():
        profit = strategy.portfolio.__liquidate__(strategy.curr_day, strategy.df)
    benchmark_strategies_exp[holding_period] = strategy


Current Day: 2010-12-21 00:00:00
3
252

Current Day: 2010-12-22 00:00:00
3
252

Current Day: 2010-12-23 00:00:00
3
252

Current Day: 2010-12-24 00:00:00
3
252

Current Day: 2010-12-27 00:00:00
3
252
NET MONEY FROM LIQUIDATION: 1645.571428571429

Current Day: 2010-12-28 00:00:00
3
252

Current Day: 2010-12-29 00:00:00
3
252

Current Day: 2010-12-30 00:00:00
3
252

Current Day: 2010-12-31 00:00:00
3
252

Current Day: 2011-01-03 00:00:00
3
252
NET MONEY FROM LIQUIDATION: 1395.25

Current Day: 2011-01-04 00:00:00
3
252

Current Day: 2011-01-05 00:00:00
3
252

Current Day: 2011-01-06 00:00:00
3
252

Current Day: 2011-01-07 00:00:00
3
252

Current Day: 2011-01-10 00:00:00
3
252
NET MONEY FROM LIQUIDATION: 3361.5

Current Day: 2011-01-11 00:00:00
3
252

Current Day: 2011-01-12 00:00:00
3
252

Current Day: 2011-01-13 00:00:00
3
252

Current Day: 2011-01-14 00:00:00
3
252

Current Day: 2011-01-17 00:00:00
3
252
NET MONEY FROM LIQUIDATION: 1281.875

Current Day: 2011-01-18 00:00:00
3
252

Curre


Current Day: 2011-08-23 00:00:00
3
252

Current Day: 2011-08-24 00:00:00
3
252

Current Day: 2011-08-25 00:00:00
3
252

Current Day: 2011-08-26 00:00:00
3
252
NET MONEY FROM LIQUIDATION: 1545.5999999999995

Current Day: 2011-08-29 00:00:00
3
252

Current Day: 2011-08-30 00:00:00
3
252

Current Day: 2011-08-31 00:00:00
3
252

Current Day: 2011-09-01 00:00:00
3
252

Current Day: 2011-09-02 00:00:00
3
252
NET MONEY FROM LIQUIDATION: 975.1499999999996

Current Day: 2011-09-05 00:00:00
3
252

Current Day: 2011-09-06 00:00:00
3
252

Current Day: 2011-09-07 00:00:00
3
252

Current Day: 2011-09-08 00:00:00
3
252

Current Day: 2011-09-09 00:00:00
3
252
NET MONEY FROM LIQUIDATION: 1216.9666666666662

Current Day: 2011-09-12 00:00:00
3
252

Current Day: 2011-09-13 00:00:00
3
252

Current Day: 2011-09-14 00:00:00
3
252

Current Day: 2011-09-15 00:00:00
3
252

Current Day: 2011-09-16 00:00:00
3
252

Current Day: 2011-09-19 00:00:00
3
252

Current Day: 2011-09-20 00:00:00
3
252

Current Day: 2011-0


Current Day: 2012-04-23 00:00:00
3
252

Current Day: 2012-04-24 00:00:00
3
252

Current Day: 2012-04-25 00:00:00
3
252

Current Day: 2012-04-26 00:00:00
3
252
NET MONEY FROM LIQUIDATION: 27.25

Current Day: 2012-04-27 00:00:00
3
252

Current Day: 2012-04-30 00:00:00
3
252

Current Day: 2012-05-01 00:00:00
3
252

Current Day: 2012-05-02 00:00:00
3
252

Current Day: 2012-05-03 00:00:00
3
252
NET MONEY FROM LIQUIDATION: -292.75

Current Day: 2012-05-04 00:00:00
3
252

Current Day: 2012-05-07 00:00:00
3
252

Current Day: 2012-05-08 00:00:00
3
252

Current Day: 2012-05-09 00:00:00
3
252

Current Day: 2012-05-10 00:00:00
3
252
NET MONEY FROM LIQUIDATION: 510.0

Current Day: 2012-05-11 00:00:00
3
252

Current Day: 2012-05-14 00:00:00
3
252

Current Day: 2012-05-15 00:00:00
3
252

Current Day: 2012-05-16 00:00:00
3
252

Current Day: 2012-05-17 00:00:00
3
252
NET MONEY FROM LIQUIDATION: 278.5

Current Day: 2012-05-18 00:00:00
3
252

Current Day: 2012-05-21 00:00:00
3
252

Current Day: 2012-05-

NET MONEY FROM LIQUIDATION: 1334.7142857142899

Current Day: 2012-12-24 00:00:00
3
252

Current Day: 2012-12-25 00:00:00
3
252

Current Day: 2012-12-26 00:00:00
3
252

Current Day: 2012-12-27 00:00:00
3
252

Current Day: 2012-12-28 00:00:00
3
252
NET MONEY FROM LIQUIDATION: 948.9890109890111

Current Day: 2012-12-31 00:00:00
3
252

Current Day: 2013-01-01 00:00:00
3
252

Current Day: 2013-01-02 00:00:00
3
252

Current Day: 2013-01-03 00:00:00
3
252

Current Day: 2013-01-04 00:00:00
3
252
NET MONEY FROM LIQUIDATION: 1239.75

Current Day: 2013-01-07 00:00:00
3
252

Current Day: 2013-01-08 00:00:00
3
252

Current Day: 2013-01-09 00:00:00
3
252

Current Day: 2013-01-10 00:00:00
3
252

Current Day: 2013-01-11 00:00:00
3
252
NET MONEY FROM LIQUIDATION: 17.75

Current Day: 2013-01-14 00:00:00
3
252

Current Day: 2013-01-15 00:00:00
3
252

Current Day: 2013-01-16 00:00:00
3
252

Current Day: 2013-01-17 00:00:00
3
252

Current Day: 2013-01-18 00:00:00
3
252
NET MONEY FROM LIQUIDATION: -323.5

C


Current Day: 2013-08-23 00:00:00
3
252

Current Day: 2013-08-26 00:00:00
3
252

Current Day: 2013-08-27 00:00:00
3
252

Current Day: 2013-08-28 00:00:00
3
252
NET MONEY FROM LIQUIDATION: -210.5

Current Day: 2013-08-29 00:00:00
3
252

Current Day: 2013-08-30 00:00:00
3
252

Current Day: 2013-09-02 00:00:00
3
252

Current Day: 2013-09-03 00:00:00
3
252

Current Day: 2013-09-04 00:00:00
3
252
NET MONEY FROM LIQUIDATION: -706.75

Current Day: 2013-09-05 00:00:00
3
252

Current Day: 2013-09-06 00:00:00
3
252

Current Day: 2013-09-09 00:00:00
3
252

Current Day: 2013-09-10 00:00:00
3
252

Current Day: 2013-09-11 00:00:00
3
252
NET MONEY FROM LIQUIDATION: -823.25

Current Day: 2013-09-12 00:00:00
3
252

Current Day: 2013-09-13 00:00:00
3
252

Current Day: 2013-09-16 00:00:00
3
252

Current Day: 2013-09-17 00:00:00
3
252

Current Day: 2013-09-18 00:00:00
3
252

Current Day: 2013-09-19 00:00:00
3
252

Current Day: 2013-09-20 00:00:00
3
252
NET MONEY FROM LIQUIDATION: 118.25

Current Day: 2013

...


Current Day: 2013-10-07 00:00:00
15
252

Current Day: 2013-10-08 00:00:00
15
252
NET MONEY FROM LIQUIDATION: 135.5

Current Day: 2013-10-09 00:00:00
15
252

Current Day: 2013-10-10 00:00:00
15
252

Current Day: 2013-10-11 00:00:00
15
252

Current Day: 2013-10-14 00:00:00
15
252

Current Day: 2013-10-15 00:00:00
15
252

Current Day: 2013-10-16 00:00:00
15
252

Current Day: 2013-10-17 00:00:00
15
252

Current Day: 2013-10-18 00:00:00
15
252

Current Day: 2013-10-21 00:00:00
15
252

Current Day: 2013-10-22 00:00:00
15
252

Current Day: 2013-10-23 00:00:00
15
252

Current Day: 2013-10-24 00:00:00
15
252

Current Day: 2013-10-25 00:00:00
15
252

Current Day: 2013-10-28 00:00:00
15
252

Current Day: 2013-10-29 00:00:00
15
252

Current Day: 2013-10-30 00:00:00
15
252

Current Day: 2013-10-31 00:00:00
15
252
NET MONEY FROM LIQUIDATION: -154.25

Current Day: 2013-11-01 00:00:00
15
252

Current Day: 2013-11-04 00:00:00
15
252

Current Day: 2013-11-05 00:00:00
15
252

Current Day: 2013-11-06 00:


Current Day: 2014-07-02 00:00:00
15
252
NET MONEY FROM LIQUIDATION: 224.75

Current Day: 2014-07-03 00:00:00
15
252

Current Day: 2014-07-04 00:00:00
15
252

Current Day: 2014-07-07 00:00:00
15
252

Current Day: 2014-07-08 00:00:00
15
252

Current Day: 2014-07-09 00:00:00
15
252

Current Day: 2014-07-10 00:00:00
15
252

Current Day: 2014-07-11 00:00:00
15
252

Current Day: 2014-07-14 00:00:00
15
252

Current Day: 2014-07-15 00:00:00
15
252

Current Day: 2014-07-16 00:00:00
15
252

Current Day: 2014-07-17 00:00:00
15
252

Current Day: 2014-07-18 00:00:00
15
252

Current Day: 2014-07-21 00:00:00
15
252

Current Day: 2014-07-22 00:00:00
15
252

Current Day: 2014-07-23 00:00:00
15
252

Current Day: 2014-07-24 00:00:00
15
252

Current Day: 2014-07-25 00:00:00
15
252

Current Day: 2014-07-28 00:00:00
15
252

Current Day: 2014-07-29 00:00:00
15
252

Current Day: 2014-07-30 00:00:00
15
252

Current Day: 2014-07-31 00:00:00
15
252

Current Day: 2014-08-01 00:00:00
15
252

Current Day: 2014-08-


Current Day: 2015-03-26 00:00:00
15
252

Current Day: 2015-03-27 00:00:00
15
252

Current Day: 2015-03-30 00:00:00
15
252

Current Day: 2015-03-31 00:00:00
15
252

Current Day: 2015-04-01 00:00:00
15
252

Current Day: 2015-04-02 00:00:00
15
252

Current Day: 2015-04-03 00:00:00
15
252

Current Day: 2015-04-06 00:00:00
15
252

Current Day: 2015-04-07 00:00:00
15
252
NET MONEY FROM LIQUIDATION: -45.25

Current Day: 2015-04-08 00:00:00
15
252

Current Day: 2015-04-09 00:00:00
15
252

Current Day: 2015-04-10 00:00:00
15
252

Current Day: 2015-04-13 00:00:00
15
252

Current Day: 2015-04-14 00:00:00
15
252

Current Day: 2015-04-15 00:00:00
15
252

Current Day: 2015-04-16 00:00:00
15
252

Current Day: 2015-04-17 00:00:00
15
252

Current Day: 2015-04-20 00:00:00
15
252

Current Day: 2015-04-21 00:00:00
15
252

Current Day: 2015-04-22 00:00:00
15
252

Current Day: 2015-04-23 00:00:00
15
252

Current Day: 2015-04-24 00:00:00
15
252

Current Day: 2015-04-27 00:00:00
15
252

Current Day: 2015-04-


Current Day: 2015-12-22 00:00:00
15
252

Current Day: 2015-12-23 00:00:00
15
252

Current Day: 2015-12-24 00:00:00
15
252

Current Day: 2015-12-25 00:00:00
15
252

Current Day: 2015-12-28 00:00:00
15
252

Current Day: 2015-12-29 00:00:00
15
252

Current Day: 2015-12-30 00:00:00
15
252

Current Day: 2015-12-31 00:00:00
15
252

Current Day: 2016-01-01 00:00:00
15
252

Current Day: 2016-01-04 00:00:00
15
252

Current Day: 2016-01-05 00:00:00
15
252

Current Day: 2016-01-06 00:00:00
15
252

Current Day: 2016-01-07 00:00:00
15
252

Current Day: 2016-01-08 00:00:00
15
252

Current Day: 2016-01-11 00:00:00
15
252

Current Day: 2016-01-12 00:00:00
15
252
NET MONEY FROM LIQUIDATION: -174.5

Current Day: 2016-01-13 00:00:00
15
252

Current Day: 2016-01-14 00:00:00
15
252

Current Day: 2016-01-15 00:00:00
15
252

Current Day: 2016-01-18 00:00:00
15
252

Current Day: 2016-01-19 00:00:00
15
252

Current Day: 2016-01-20 00:00:00
15
252

Current Day: 2016-01-21 00:00:00
15
252

Current Day: 2016-01-


Current Day: 2016-09-16 00:00:00
15
252

Current Day: 2016-09-19 00:00:00
15
252

Current Day: 2016-09-20 00:00:00
15
252

Current Day: 2016-09-21 00:00:00
15
252

Current Day: 2016-09-22 00:00:00
15
252

Current Day: 2016-09-23 00:00:00
15
252

Current Day: 2016-09-26 00:00:00
15
252

Current Day: 2016-09-27 00:00:00
15
252

Current Day: 2016-09-28 00:00:00
15
252

Current Day: 2016-09-29 00:00:00
15
252

Current Day: 2016-09-30 00:00:00
15
252

Current Day: 2016-10-03 00:00:00
15
252

Current Day: 2016-10-04 00:00:00
15
252

Current Day: 2016-10-05 00:00:00
15
252

Current Day: 2016-10-06 00:00:00
15
252

Current Day: 2016-10-07 00:00:00
15
252

Current Day: 2016-10-10 00:00:00
15
252
NET MONEY FROM LIQUIDATION: -1.0

Current Day: 2016-10-11 00:00:00
15
252

Current Day: 2016-10-12 00:00:00
15
252

Current Day: 2016-10-13 00:00:00
15
252

Current Day: 2016-10-14 00:00:00
15
252

Current Day: 2016-10-17 00:00:00
15
252

Current Day: 2016-10-18 00:00:00
15
252

Current Day: 2016-10-19

In [72]:
benchmark_strategies_fixed = dict()
for holding_period in [3, 5, 10, 15]:
    for wdw_length in [504, 756, 1008]:
        strategy = PCA_Strategy(final_train_df, 15, 100000, False)
        strategy.__run__(holding_period, wdw_length, wdw_length)
        if not strategy.portfolio.__is_empty__():
            profit = strategy.portfolio.__liquidate__(strategy.curr_day, strategy.df)
        benchmark_strategies_fixed[str(holding_period) + "-" + str(wdw_length)] = strategy


Current Day: 2011-12-08 00:00:00
3
504

Current Day: 2011-12-09 00:00:00
3
504

Current Day: 2011-12-12 00:00:00
3
504

Current Day: 2011-12-13 00:00:00
3
504

Current Day: 2011-12-14 00:00:00
3
504
NET MONEY FROM LIQUIDATION: 525.4000000000015

Current Day: 2011-12-15 00:00:00
3
504

Current Day: 2011-12-16 00:00:00
3
504

Current Day: 2011-12-19 00:00:00
3
504

Current Day: 2011-12-20 00:00:00
3
504

Current Day: 2011-12-21 00:00:00
3
504

Current Day: 2011-12-22 00:00:00
3
504
NET MONEY FROM LIQUIDATION: 378.7904761904774

Current Day: 2011-12-23 00:00:00
3
504

Current Day: 2011-12-26 00:00:00
3
504

Current Day: 2011-12-27 00:00:00
3
504

Current Day: 2011-12-28 00:00:00
3
504

Current Day: 2011-12-29 00:00:00
3
504
NET MONEY FROM LIQUIDATION: -152.05714285714203

Current Day: 2011-12-30 00:00:00
3
504

Current Day: 2012-01-02 00:00:00
3
504

Current Day: 2012-01-03 00:00:00
3
504

Current Day: 2012-01-04 00:00:00
3
504

Current Day: 2012-01-05 00:00:00
3
504
NET MONEY FROM LIQUI


Current Day: 2012-08-09 00:00:00
3
504

Current Day: 2012-08-10 00:00:00
3
504
NET MONEY FROM LIQUIDATION: 1530.75

Current Day: 2012-08-13 00:00:00
3
504

Current Day: 2012-08-14 00:00:00
3
504

Current Day: 2012-08-15 00:00:00
3
504

Current Day: 2012-08-16 00:00:00
3
504

Current Day: 2012-08-17 00:00:00
3
504
NET MONEY FROM LIQUIDATION: -81.75

Current Day: 2012-08-20 00:00:00
3
504

Current Day: 2012-08-21 00:00:00
3
504

Current Day: 2012-08-22 00:00:00
3
504

Current Day: 2012-08-23 00:00:00
3
504

Current Day: 2012-08-24 00:00:00
3
504
NET MONEY FROM LIQUIDATION: -426.5

Current Day: 2012-08-27 00:00:00
3
504

Current Day: 2012-08-28 00:00:00
3
504

Current Day: 2012-08-29 00:00:00
3
504

Current Day: 2012-08-30 00:00:00
3
504

Current Day: 2012-08-31 00:00:00
3
504
NET MONEY FROM LIQUIDATION: 565.5

Current Day: 2012-09-03 00:00:00
3
504

Current Day: 2012-09-04 00:00:00
3
504

Current Day: 2012-09-05 00:00:00
3
504

Current Day: 2012-09-06 00:00:00
3
504

Current Day: 2012-0


Current Day: 2013-04-11 00:00:00
3
504

Current Day: 2013-04-12 00:00:00
3
504
NET MONEY FROM LIQUIDATION: -545.0

Current Day: 2013-04-15 00:00:00
3
504

Current Day: 2013-04-16 00:00:00
3
504

Current Day: 2013-04-17 00:00:00
3
504

Current Day: 2013-04-18 00:00:00
3
504

Current Day: 2013-04-19 00:00:00
3
504
NET MONEY FROM LIQUIDATION: -1584.5

Current Day: 2013-04-22 00:00:00
3
504

Current Day: 2013-04-23 00:00:00
3
504

Current Day: 2013-04-24 00:00:00
3
504

Current Day: 2013-04-25 00:00:00
3
504

Current Day: 2013-04-26 00:00:00
3
504
NET MONEY FROM LIQUIDATION: -1278.75

Current Day: 2013-04-29 00:00:00
3
504

Current Day: 2013-04-30 00:00:00
3
504

Current Day: 2013-05-01 00:00:00
3
504

Current Day: 2013-05-02 00:00:00
3
504

Current Day: 2013-05-03 00:00:00
3
504
NET MONEY FROM LIQUIDATION: -63.25

Current Day: 2013-05-06 00:00:00
3
504

Current Day: 2013-05-07 00:00:00
3
504

Current Day: 2013-05-08 00:00:00
3
504

Current Day: 2013-05-09 00:00:00
3
504

Current Day: 201


Current Day: 2013-12-12 00:00:00
3
504

Current Day: 2013-12-13 00:00:00
3
504
NET MONEY FROM LIQUIDATION: 363.5

Current Day: 2013-12-16 00:00:00
3
504

Current Day: 2013-12-17 00:00:00
3
504

Current Day: 2013-12-18 00:00:00
3
504

Current Day: 2013-12-19 00:00:00
3
504

Current Day: 2013-12-20 00:00:00
3
504
NET MONEY FROM LIQUIDATION: 93.03571428571558

Current Day: 2013-12-23 00:00:00
3
504

Current Day: 2013-12-24 00:00:00
3
504

Current Day: 2013-12-25 00:00:00
3
504

Current Day: 2013-12-26 00:00:00
3
504

Current Day: 2013-12-27 00:00:00
3
504
NET MONEY FROM LIQUIDATION: -853.25

Current Day: 2013-12-30 00:00:00
3
504

Current Day: 2013-12-31 00:00:00
3
504

Current Day: 2014-01-01 00:00:00
3
504

Current Day: 2014-01-02 00:00:00
3
504

Current Day: 2014-01-03 00:00:00
3
504
NET MONEY FROM LIQUIDATION: -324.75

Current Day: 2014-01-06 00:00:00
3
504

Current Day: 2014-01-07 00:00:00
3
504

Current Day: 2014-01-08 00:00:00
3
504

Current Day: 2014-01-09 00:00:00
3
504

Current


Current Day: 2014-08-14 00:00:00
3
504
NET MONEY FROM LIQUIDATION: -377.25

Current Day: 2014-08-15 00:00:00
3
504

Current Day: 2014-08-18 00:00:00
3
504

Current Day: 2014-08-19 00:00:00
3
504

Current Day: 2014-08-20 00:00:00
3
504

Current Day: 2014-08-21 00:00:00
3
504
NET MONEY FROM LIQUIDATION: -406.25

Current Day: 2014-08-22 00:00:00
3
504

Current Day: 2014-08-25 00:00:00
3
504

Current Day: 2014-08-26 00:00:00
3
504

Current Day: 2014-08-27 00:00:00
3
504

Current Day: 2014-08-28 00:00:00
3
504
NET MONEY FROM LIQUIDATION: 36.75

Current Day: 2014-08-29 00:00:00
3
504

Current Day: 2014-09-01 00:00:00
3
504

Current Day: 2014-09-02 00:00:00
3
504

Current Day: 2014-09-03 00:00:00
3
504

Current Day: 2014-09-04 00:00:00
3
504
NET MONEY FROM LIQUIDATION: -254.0

Current Day: 2014-09-05 00:00:00
3
504

Current Day: 2014-09-08 00:00:00
3
504

Current Day: 2014-09-09 00:00:00
3
504

Current Day: 2014-09-10 00:00:00
3
504

Current Day: 2014-09-11 00:00:00
3
504
NET MONEY FROM LIQU

...


Current Day: 2013-06-20 00:00:00
15
756

Current Day: 2013-06-21 00:00:00
15
756

Current Day: 2013-06-24 00:00:00
15
756

Current Day: 2013-06-25 00:00:00
15
756

Current Day: 2013-06-26 00:00:00
15
756

Current Day: 2013-06-27 00:00:00
15
756

Current Day: 2013-06-28 00:00:00
15
756

Current Day: 2013-07-01 00:00:00
15
756

Current Day: 2013-07-02 00:00:00
15
756
NET MONEY FROM LIQUIDATION: -619.5

Current Day: 2013-07-03 00:00:00
15
756

Current Day: 2013-07-04 00:00:00
15
756

Current Day: 2013-07-05 00:00:00
15
756

Current Day: 2013-07-08 00:00:00
15
756

Current Day: 2013-07-09 00:00:00
15
756

Current Day: 2013-07-10 00:00:00
15
756

Current Day: 2013-07-11 00:00:00
15
756

Current Day: 2013-07-12 00:00:00
15
756

Current Day: 2013-07-15 00:00:00
15
756

Current Day: 2013-07-16 00:00:00
15
756

Current Day: 2013-07-17 00:00:00
15
756

Current Day: 2013-07-18 00:00:00
15
756

Current Day: 2013-07-19 00:00:00
15
756

Current Day: 2013-07-22 00:00:00
15
756

Current Day: 2013-07-


Current Day: 2014-03-17 00:00:00
15
756

Current Day: 2014-03-18 00:00:00
15
756

Current Day: 2014-03-19 00:00:00
15
756

Current Day: 2014-03-20 00:00:00
15
756

Current Day: 2014-03-21 00:00:00
15
756

Current Day: 2014-03-24 00:00:00
15
756

Current Day: 2014-03-25 00:00:00
15
756

Current Day: 2014-03-26 00:00:00
15
756

Current Day: 2014-03-27 00:00:00
15
756

Current Day: 2014-03-28 00:00:00
15
756

Current Day: 2014-03-31 00:00:00
15
756

Current Day: 2014-04-01 00:00:00
15
756

Current Day: 2014-04-02 00:00:00
15
756

Current Day: 2014-04-03 00:00:00
15
756

Current Day: 2014-04-04 00:00:00
15
756

Current Day: 2014-04-07 00:00:00
15
756

Current Day: 2014-04-08 00:00:00
15
756
NET MONEY FROM LIQUIDATION: 325.25

Current Day: 2014-04-09 00:00:00
15
756

Current Day: 2014-04-10 00:00:00
15
756

Current Day: 2014-04-11 00:00:00
15
756

Current Day: 2014-04-14 00:00:00
15
756

Current Day: 2014-04-15 00:00:00
15
756

Current Day: 2014-04-16 00:00:00
15
756

Current Day: 2014-04-


Current Day: 2014-12-11 00:00:00
15
756

Current Day: 2014-12-12 00:00:00
15
756

Current Day: 2014-12-15 00:00:00
15
756

Current Day: 2014-12-16 00:00:00
15
756

Current Day: 2014-12-17 00:00:00
15
756

Current Day: 2014-12-18 00:00:00
15
756
NET MONEY FROM LIQUIDATION: -394.41666666666697

Current Day: 2014-12-19 00:00:00
15
756

Current Day: 2014-12-22 00:00:00
15
756

Current Day: 2014-12-23 00:00:00
15
756

Current Day: 2014-12-24 00:00:00
15
756

Current Day: 2014-12-25 00:00:00
15
756

Current Day: 2014-12-26 00:00:00
15
756

Current Day: 2014-12-29 00:00:00
15
756

Current Day: 2014-12-30 00:00:00
15
756

Current Day: 2014-12-31 00:00:00
15
756

Current Day: 2015-01-01 00:00:00
15
756

Current Day: 2015-01-02 00:00:00
15
756

Current Day: 2015-01-05 00:00:00
15
756

Current Day: 2015-01-06 00:00:00
15
756

Current Day: 2015-01-07 00:00:00
15
756

Current Day: 2015-01-08 00:00:00
15
756

Current Day: 2015-01-09 00:00:00
15
756

Current Day: 2015-01-12 00:00:00
15
756
NET MONEY


Current Day: 2015-09-04 00:00:00
15
756

Current Day: 2015-09-07 00:00:00
15
756

Current Day: 2015-09-08 00:00:00
15
756

Current Day: 2015-09-09 00:00:00
15
756

Current Day: 2015-09-10 00:00:00
15
756

Current Day: 2015-09-11 00:00:00
15
756

Current Day: 2015-09-14 00:00:00
15
756

Current Day: 2015-09-15 00:00:00
15
756

Current Day: 2015-09-16 00:00:00
15
756

Current Day: 2015-09-17 00:00:00
15
756

Current Day: 2015-09-18 00:00:00
15
756

Current Day: 2015-09-21 00:00:00
15
756

Current Day: 2015-09-22 00:00:00
15
756

Current Day: 2015-09-23 00:00:00
15
756

Current Day: 2015-09-24 00:00:00
15
756

Current Day: 2015-09-25 00:00:00
15
756

Current Day: 2015-09-28 00:00:00
15
756

Current Day: 2015-09-29 00:00:00
15
756

Current Day: 2015-09-30 00:00:00
15
756

Current Day: 2015-10-01 00:00:00
15
756

Current Day: 2015-10-02 00:00:00
15
756

Current Day: 2015-10-05 00:00:00
15
756

Current Day: 2015-10-06 00:00:00
15
756

Current Day: 2015-10-07 00:00:00
15
756

Current Day: 20

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [73]:
strategies = dict()
for wdw_length in [504, 756, 1008]:
    for holding_period in [3, 5, 10, 15]:
        strategy = PCA_HMM_Strategy(final_train_df, 3, 15, 100000, False)
        strategy.__run__(holding_period, wdw_length, wdw_length)
        if not strategy.portfolio.__is_empty__():
            strategy.portfolio.__liquidate__(strategy.curr_day, strategy.df)
            
        strategies[str(holding_period) + "-"  + str(wdw_length)] = strategy



Current Day: 2011-12-08 00:00:00
3
504

Current Day: 2011-12-09 00:00:00
3
504

Current Day: 2011-12-12 00:00:00
3
504

Current Day: 2011-12-13 00:00:00
3
504

Current Day: 2011-12-14 00:00:00
3
504
NET MONEY FROM LIQUIDATION: -786.9499999999989

Current Day: 2011-12-15 00:00:00
3
504

Current Day: 2011-12-16 00:00:00
3
504

Current Day: 2011-12-19 00:00:00
3
504

Current Day: 2011-12-20 00:00:00
3
504

Current Day: 2011-12-21 00:00:00
3
504
NET MONEY FROM LIQUIDATION: -1148.7999999999993

Current Day: 2011-12-22 00:00:00
3
504

Current Day: 2011-12-23 00:00:00
3
504

Current Day: 2011-12-26 00:00:00
3
504

Current Day: 2011-12-27 00:00:00
3
504

Current Day: 2011-12-28 00:00:00
3
504
NET MONEY FROM LIQUIDATION: -1195.442857142858

Current Day: 2011-12-29 00:00:00
3
504

Current Day: 2011-12-30 00:00:00
3
504

Current Day: 2012-01-02 00:00:00
3
504

Current Day: 2012-01-03 00:00:00
3
504

Current Day: 2012-01-04 00:00:00
3
504
NET MONEY FROM LIQUIDATION: 836.75

Current Day: 2012-01-0


Current Day: 2012-08-01 00:00:00
3
504

Current Day: 2012-08-02 00:00:00
3
504

Current Day: 2012-08-03 00:00:00
3
504

Current Day: 2012-08-06 00:00:00
3
504
NET MONEY FROM LIQUIDATION: 322.5

Current Day: 2012-08-07 00:00:00
3
504

Current Day: 2012-08-08 00:00:00
3
504

Current Day: 2012-08-09 00:00:00
3
504

Current Day: 2012-08-10 00:00:00
3
504

Current Day: 2012-08-13 00:00:00
3
504
NET MONEY FROM LIQUIDATION: -1899.5

Current Day: 2012-08-14 00:00:00
3
504

Current Day: 2012-08-15 00:00:00
3
504

Current Day: 2012-08-16 00:00:00
3
504

Current Day: 2012-08-17 00:00:00
3
504

Current Day: 2012-08-20 00:00:00
3
504
NET MONEY FROM LIQUIDATION: 1275.5

Current Day: 2012-08-21 00:00:00
3
504

Current Day: 2012-08-22 00:00:00
3
504

Current Day: 2012-08-23 00:00:00
3
504

Current Day: 2012-08-24 00:00:00
3
504

Current Day: 2012-08-27 00:00:00
3
504
NET MONEY FROM LIQUIDATION: -93.0

Current Day: 2012-08-28 00:00:00
3
504

Current Day: 2012-08-29 00:00:00
3
504

Current Day: 2012-08


Current Day: 2013-03-28 00:00:00
3
504
NET MONEY FROM LIQUIDATION: -468.0

Current Day: 2013-03-29 00:00:00
3
504

Current Day: 2013-04-01 00:00:00
3
504
NET MONEY FROM LIQUIDATION: -1677.5

Current Day: 2013-04-02 00:00:00
3
504

Current Day: 2013-04-03 00:00:00
3
504

Current Day: 2013-04-04 00:00:00
3
504

Current Day: 2013-04-05 00:00:00
3
504

Current Day: 2013-04-08 00:00:00
3
504
NET MONEY FROM LIQUIDATION: -277.75

Current Day: 2013-04-09 00:00:00
3
504

Current Day: 2013-04-10 00:00:00
3
504

Current Day: 2013-04-11 00:00:00
3
504

Current Day: 2013-04-12 00:00:00
3
504

Current Day: 2013-04-15 00:00:00
3
504
NET MONEY FROM LIQUIDATION: -277.5

Current Day: 2013-04-16 00:00:00
3
504

Current Day: 2013-04-17 00:00:00
3
504
NET MONEY FROM LIQUIDATION: -475.5

Current Day: 2013-04-18 00:00:00
3
504

Current Day: 2013-04-19 00:00:00
3
504

Current Day: 2013-04-22 00:00:00
3
504
NET MONEY FROM LIQUIDATION: -516.0

Current Day: 2013-04-23 00:00:00
3
504

Current Day: 2013-04-24 00:


Current Day: 2013-11-15 00:00:00
3
504
NET MONEY FROM LIQUIDATION: 604.5

Current Day: 2013-11-18 00:00:00
3
504

Current Day: 2013-11-19 00:00:00
3
504
NET MONEY FROM LIQUIDATION: -573.25

Current Day: 2013-11-20 00:00:00
3
504

Current Day: 2013-11-21 00:00:00
3
504

Current Day: 2013-11-22 00:00:00
3
504

Current Day: 2013-11-25 00:00:00
3
504

Current Day: 2013-11-26 00:00:00
3
504
NET MONEY FROM LIQUIDATION: 435.0

Current Day: 2013-11-27 00:00:00
3
504

Current Day: 2013-11-28 00:00:00
3
504

Current Day: 2013-11-29 00:00:00
3
504

Current Day: 2013-12-02 00:00:00
3
504

Current Day: 2013-12-03 00:00:00
3
504
NET MONEY FROM LIQUIDATION: -346.25

Current Day: 2013-12-04 00:00:00
3
504

Current Day: 2013-12-05 00:00:00
3
504

Current Day: 2013-12-06 00:00:00
3
504

Current Day: 2013-12-09 00:00:00
3
504

Current Day: 2013-12-10 00:00:00
3
504
NET MONEY FROM LIQUIDATION: 665.5

Current Day: 2013-12-11 00:00:00
3
504

Current Day: 2013-12-12 00:00:00
3
504

Current Day: 2013-12-13 0


Current Day: 2014-07-10 00:00:00
3
504

Current Day: 2014-07-11 00:00:00
3
504

Current Day: 2014-07-14 00:00:00
3
504
NET MONEY FROM LIQUIDATION: -448.25

Current Day: 2014-07-15 00:00:00
3
504

Current Day: 2014-07-16 00:00:00
3
504

Current Day: 2014-07-17 00:00:00
3
504

Current Day: 2014-07-18 00:00:00
3
504
NET MONEY FROM LIQUIDATION: -412.75

Current Day: 2014-07-21 00:00:00
3
504

Current Day: 2014-07-22 00:00:00
3
504
NET MONEY FROM LIQUIDATION: -297.0

Current Day: 2014-07-23 00:00:00
3
504

Current Day: 2014-07-24 00:00:00
3
504

Current Day: 2014-07-25 00:00:00
3
504

Current Day: 2014-07-28 00:00:00
3
504

Current Day: 2014-07-29 00:00:00
3
504
NET MONEY FROM LIQUIDATION: -50.0

Current Day: 2014-07-30 00:00:00
3
504

Current Day: 2014-07-31 00:00:00
3
504

Current Day: 2014-08-01 00:00:00
3
504

Current Day: 2014-08-04 00:00:00
3
504

Current Day: 2014-08-05 00:00:00
3
504
NET MONEY FROM LIQUIDATION: -507.0

Current Day: 2014-08-06 00:00:00
3
504

Current Day: 2014-08-07

...


Current Day: 2014-01-01 00:00:00
15
1008

Current Day: 2014-01-02 00:00:00
15
1008

Current Day: 2014-01-03 00:00:00
15
1008

Current Day: 2014-01-06 00:00:00
15
1008

Current Day: 2014-01-07 00:00:00
15
1008

Current Day: 2014-01-08 00:00:00
15
1008

Current Day: 2014-01-09 00:00:00
15
1008
NET MONEY FROM LIQUIDATION: 504.75

Current Day: 2014-01-10 00:00:00
15
1008

Current Day: 2014-01-13 00:00:00
15
1008
NET MONEY FROM LIQUIDATION: 544.0

Current Day: 2014-01-14 00:00:00
15
1008

Current Day: 2014-01-15 00:00:00
15
1008

Current Day: 2014-01-16 00:00:00
15
1008

Current Day: 2014-01-17 00:00:00
15
1008

Current Day: 2014-01-20 00:00:00
15
1008

Current Day: 2014-01-21 00:00:00
15
1008

Current Day: 2014-01-22 00:00:00
15
1008

Current Day: 2014-01-23 00:00:00
15
1008

Current Day: 2014-01-24 00:00:00
15
1008

Current Day: 2014-01-27 00:00:00
15
1008

Current Day: 2014-01-28 00:00:00
15
1008

Current Day: 2014-01-29 00:00:00
15
1008

Current Day: 2014-01-30 00:00:00
15
1008

Curren


Current Day: 2014-09-11 00:00:00
15
1008

Current Day: 2014-09-12 00:00:00
15
1008

Current Day: 2014-09-15 00:00:00
15
1008
NET MONEY FROM LIQUIDATION: -420.75

Current Day: 2014-09-16 00:00:00
15
1008

Current Day: 2014-09-17 00:00:00
15
1008

Current Day: 2014-09-18 00:00:00
15
1008

Current Day: 2014-09-19 00:00:00
15
1008

Current Day: 2014-09-22 00:00:00
15
1008

Current Day: 2014-09-23 00:00:00
15
1008

Current Day: 2014-09-24 00:00:00
15
1008

Current Day: 2014-09-25 00:00:00
15
1008

Current Day: 2014-09-26 00:00:00
15
1008

Current Day: 2014-09-29 00:00:00
15
1008

Current Day: 2014-09-30 00:00:00
15
1008

Current Day: 2014-10-01 00:00:00
15
1008

Current Day: 2014-10-02 00:00:00
15
1008

Current Day: 2014-10-03 00:00:00
15
1008

Current Day: 2014-10-06 00:00:00
15
1008
NET MONEY FROM LIQUIDATION: 109.75

Current Day: 2014-10-07 00:00:00
15
1008

Current Day: 2014-10-08 00:00:00
15
1008
NET MONEY FROM LIQUIDATION: -286.0

Current Day: 2014-10-09 00:00:00
15
1008

Current Day

NET MONEY FROM LIQUIDATION: -349.75

Current Day: 2015-05-15 00:00:00
15
1008

Current Day: 2015-05-18 00:00:00
15
1008

Current Day: 2015-05-19 00:00:00
15
1008

Current Day: 2015-05-20 00:00:00
15
1008

Current Day: 2015-05-21 00:00:00
15
1008

Current Day: 2015-05-22 00:00:00
15
1008

Current Day: 2015-05-25 00:00:00
15
1008

Current Day: 2015-05-26 00:00:00
15
1008

Current Day: 2015-05-27 00:00:00
15
1008

Current Day: 2015-05-28 00:00:00
15
1008

Current Day: 2015-05-29 00:00:00
15
1008

Current Day: 2015-06-01 00:00:00
15
1008

Current Day: 2015-06-02 00:00:00
15
1008

Current Day: 2015-06-03 00:00:00
15
1008

Current Day: 2015-06-04 00:00:00
15
1008

Current Day: 2015-06-05 00:00:00
15
1008

Current Day: 2015-06-08 00:00:00
15
1008
NET MONEY FROM LIQUIDATION: 1587.75

Current Day: 2015-06-09 00:00:00
15
1008

Current Day: 2015-06-10 00:00:00
15
1008
NET MONEY FROM LIQUIDATION: 769.5

Current Day: 2015-06-11 00:00:00
15
1008

Current Day: 2015-06-12 00:00:00
15
1008

Current Day


Current Day: 2016-01-20 00:00:00
15
1008

Current Day: 2016-01-21 00:00:00
15
1008

Current Day: 2016-01-22 00:00:00
15
1008

Current Day: 2016-01-25 00:00:00
15
1008

Current Day: 2016-01-26 00:00:00
15
1008

Current Day: 2016-01-27 00:00:00
15
1008

Current Day: 2016-01-28 00:00:00
15
1008

Current Day: 2016-01-29 00:00:00
15
1008
NET MONEY FROM LIQUIDATION: 370.5

Current Day: 2016-02-01 00:00:00
15
1008

Current Day: 2016-02-02 00:00:00
15
1008

Current Day: 2016-02-03 00:00:00
15
1008

Current Day: 2016-02-04 00:00:00
15
1008

Current Day: 2016-02-05 00:00:00
15
1008

Current Day: 2016-02-08 00:00:00
15
1008

Current Day: 2016-02-09 00:00:00
15
1008

Current Day: 2016-02-10 00:00:00
15
1008

Current Day: 2016-02-11 00:00:00
15
1008

Current Day: 2016-02-12 00:00:00
15
1008

Current Day: 2016-02-15 00:00:00
15
1008

Current Day: 2016-02-16 00:00:00
15
1008

Current Day: 2016-02-17 00:00:00
15
1008

Current Day: 2016-02-18 00:00:00
15
1008

Current Day: 2016-02-19 00:00:00
15
1008



Current Day: 2016-09-19 00:00:00
15
1008

Current Day: 2016-09-20 00:00:00
15
1008

Current Day: 2016-09-21 00:00:00
15
1008

Current Day: 2016-09-22 00:00:00
15
1008

Current Day: 2016-09-23 00:00:00
15
1008

Current Day: 2016-09-26 00:00:00
15
1008
NET MONEY FROM LIQUIDATION: -215.25

Current Day: 2016-09-27 00:00:00
15
1008

Current Day: 2016-09-28 00:00:00
15
1008

Current Day: 2016-09-29 00:00:00
15
1008

Current Day: 2016-09-30 00:00:00
15
1008
NET MONEY FROM LIQUIDATION: 228.0

Current Day: 2016-10-03 00:00:00
15
1008

Current Day: 2016-10-04 00:00:00
15
1008
NET MONEY FROM LIQUIDATION: 239.5

Current Day: 2016-10-05 00:00:00
15
1008

Current Day: 2016-10-06 00:00:00
15
1008
NET MONEY FROM LIQUIDATION: 374.75

Current Day: 2016-10-07 00:00:00
15
1008

Current Day: 2016-10-10 00:00:00
15
1008

Current Day: 2016-10-11 00:00:00
15
1008

Current Day: 2016-10-12 00:00:00
15
1008
NET MONEY FROM LIQUIDATION: -182.25

Current Day: 2016-10-13 00:00:00
15
1008

Current Day: 2016-10-14 00

In [75]:
expanding_strats = dict()
for holding_period in [3, 5, 10, 15]:
    strategy = PCA_HMM_Strategy(final_train_df, 3, 15, 100000, True)
    strategy.__run__(holding_period, 520, 520)
    if not strategy.portfolio.__is_empty__():
        strategy.portfolio.__liquidate__(strategy.curr_day, strategy.df)
    expanding_strats[holding_period] = strategy


Current Day: 2011-12-30 00:00:00
3
520

Current Day: 2012-01-02 00:00:00
3
520

Current Day: 2012-01-03 00:00:00
3
520

Current Day: 2012-01-04 00:00:00
3
520

Current Day: 2012-01-05 00:00:00
3
520
NET MONEY FROM LIQUIDATION: 1438.0

Current Day: 2012-01-06 00:00:00
3
520

Current Day: 2012-01-09 00:00:00
3
520

Current Day: 2012-01-10 00:00:00
3
520

Current Day: 2012-01-11 00:00:00
3
520

Current Day: 2012-01-12 00:00:00
3
520
NET MONEY FROM LIQUIDATION: -76.75

Current Day: 2012-01-13 00:00:00
3
520

Current Day: 2012-01-16 00:00:00
3
520

Current Day: 2012-01-17 00:00:00
3
520

Current Day: 2012-01-18 00:00:00
3
520

Current Day: 2012-01-19 00:00:00
3
520
NET MONEY FROM LIQUIDATION: 645.75

Current Day: 2012-01-20 00:00:00
3
520

Current Day: 2012-01-23 00:00:00
3
520

Current Day: 2012-01-24 00:00:00
3
520

Current Day: 2012-01-25 00:00:00
3
520

Current Day: 2012-01-26 00:00:00
3
520
NET MONEY FROM LIQUIDATION: -378.25

Current Day: 2012-01-27 00:00:00
3
520

Current Day: 2012-


Current Day: 2012-08-27 00:00:00
3
520
NET MONEY FROM LIQUIDATION: -61.5

Current Day: 2012-08-28 00:00:00
3
520

Current Day: 2012-08-29 00:00:00
3
520

Current Day: 2012-08-30 00:00:00
3
520

Current Day: 2012-08-31 00:00:00
3
520

Current Day: 2012-09-03 00:00:00
3
520
NET MONEY FROM LIQUIDATION: 1328.875

Current Day: 2012-09-04 00:00:00
3
520

Current Day: 2012-09-05 00:00:00
3
520

Current Day: 2012-09-06 00:00:00
3
520

Current Day: 2012-09-07 00:00:00
3
520

Current Day: 2012-09-10 00:00:00
3
520
NET MONEY FROM LIQUIDATION: 18.75

Current Day: 2012-09-11 00:00:00
3
520

Current Day: 2012-09-12 00:00:00
3
520

Current Day: 2012-09-13 00:00:00
3
520

Current Day: 2012-09-14 00:00:00
3
520

Current Day: 2012-09-17 00:00:00
3
520
NET MONEY FROM LIQUIDATION: -852.75

Current Day: 2012-09-18 00:00:00
3
520

Current Day: 2012-09-19 00:00:00
3
520

Current Day: 2012-09-20 00:00:00
3
520

Current Day: 2012-09-21 00:00:00
3
520

Current Day: 2012-09-24 00:00:00
3
520
NET MONEY FROM LIQU

NET MONEY FROM LIQUIDATION: 642.25

Current Day: 2013-04-23 00:00:00
3
520

Current Day: 2013-04-24 00:00:00
3
520

Current Day: 2013-04-25 00:00:00
3
520

Current Day: 2013-04-26 00:00:00
3
520

Current Day: 2013-04-29 00:00:00
3
520
NET MONEY FROM LIQUIDATION: 395.25

Current Day: 2013-04-30 00:00:00
3
520

Current Day: 2013-05-01 00:00:00
3
520

Current Day: 2013-05-02 00:00:00
3
520

Current Day: 2013-05-03 00:00:00
3
520

Current Day: 2013-05-06 00:00:00
3
520
NET MONEY FROM LIQUIDATION: -180.75

Current Day: 2013-05-07 00:00:00
3
520

Current Day: 2013-05-08 00:00:00
3
520

Current Day: 2013-05-09 00:00:00
3
520

Current Day: 2013-05-10 00:00:00
3
520

Current Day: 2013-05-13 00:00:00
3
520
NET MONEY FROM LIQUIDATION: -598.5

Current Day: 2013-05-14 00:00:00
3
520

Current Day: 2013-05-15 00:00:00
3
520
NET MONEY FROM LIQUIDATION: -176.75

Current Day: 2013-05-16 00:00:00
3
520

Current Day: 2013-05-17 00:00:00
3
520

Current Day: 2013-05-20 00:00:00
3
520

Current Day: 2013-05-2


Current Day: 2013-12-16 00:00:00
3
520
NET MONEY FROM LIQUIDATION: 224.51785714285688

Current Day: 2013-12-17 00:00:00
3
520

Current Day: 2013-12-18 00:00:00
3
520

Current Day: 2013-12-19 00:00:00
3
520

Current Day: 2013-12-20 00:00:00
3
520

Current Day: 2013-12-23 00:00:00
3
520
NET MONEY FROM LIQUIDATION: -484.28571428571433

Current Day: 2013-12-24 00:00:00
3
520

Current Day: 2013-12-25 00:00:00
3
520

Current Day: 2013-12-26 00:00:00
3
520

Current Day: 2013-12-27 00:00:00
3
520

Current Day: 2013-12-30 00:00:00
3
520
NET MONEY FROM LIQUIDATION: 345.2142857142858

Current Day: 2013-12-31 00:00:00
3
520

Current Day: 2014-01-01 00:00:00
3
520

Current Day: 2014-01-02 00:00:00
3
520

Current Day: 2014-01-03 00:00:00
3
520

Current Day: 2014-01-06 00:00:00
3
520
NET MONEY FROM LIQUIDATION: -383.5

Current Day: 2014-01-07 00:00:00
3
520

Current Day: 2014-01-08 00:00:00
3
520

Current Day: 2014-01-09 00:00:00
3
520

Current Day: 2014-01-10 00:00:00
3
520
NET MONEY FROM LIQUIDATI


Current Day: 2014-08-12 00:00:00
3
520

Current Day: 2014-08-13 00:00:00
3
520

Current Day: 2014-08-14 00:00:00
3
520

Current Day: 2014-08-15 00:00:00
3
520
NET MONEY FROM LIQUIDATION: 207.0

Current Day: 2014-08-18 00:00:00
3
520

Current Day: 2014-08-19 00:00:00
3
520

Current Day: 2014-08-20 00:00:00
3
520

Current Day: 2014-08-21 00:00:00
3
520

Current Day: 2014-08-22 00:00:00
3
520
NET MONEY FROM LIQUIDATION: -682.75

Current Day: 2014-08-25 00:00:00
3
520

Current Day: 2014-08-26 00:00:00
3
520

Current Day: 2014-08-27 00:00:00
3
520

Current Day: 2014-08-28 00:00:00
3
520

Current Day: 2014-08-29 00:00:00
3
520
NET MONEY FROM LIQUIDATION: -436.25

Current Day: 2014-09-01 00:00:00
3
520

Current Day: 2014-09-02 00:00:00
3
520

Current Day: 2014-09-03 00:00:00
3
520
NET MONEY FROM LIQUIDATION: -456.0

Current Day: 2014-09-04 00:00:00
3
520

Current Day: 2014-09-05 00:00:00
3
520
NET MONEY FROM LIQUIDATION: -455.5

Current Day: 2014-09-08 00:00:00
3
520

Current Day: 2014-09-09

...


Current Day: 2014-04-18 00:00:00
15
520

Current Day: 2014-04-21 00:00:00
15
520
NET MONEY FROM LIQUIDATION: 224.25

Current Day: 2014-04-22 00:00:00
15
520

Current Day: 2014-04-23 00:00:00
15
520

Current Day: 2014-04-24 00:00:00
15
520

Current Day: 2014-04-25 00:00:00
15
520

Current Day: 2014-04-28 00:00:00
15
520

Current Day: 2014-04-29 00:00:00
15
520

Current Day: 2014-04-30 00:00:00
15
520

Current Day: 2014-05-01 00:00:00
15
520
NET MONEY FROM LIQUIDATION: -292.75

Current Day: 2014-05-02 00:00:00
15
520

Current Day: 2014-05-05 00:00:00
15
520

Current Day: 2014-05-06 00:00:00
15
520

Current Day: 2014-05-07 00:00:00
15
520

Current Day: 2014-05-08 00:00:00
15
520

Current Day: 2014-05-09 00:00:00
15
520
NET MONEY FROM LIQUIDATION: 696.0

Current Day: 2014-05-12 00:00:00
15
520

Current Day: 2014-05-13 00:00:00
15
520

Current Day: 2014-05-14 00:00:00
15
520

Current Day: 2014-05-15 00:00:00
15
520

Current Day: 2014-05-16 00:00:00
15
520

Current Day: 2014-05-19 00:00:00



Current Day: 2014-12-26 00:00:00
15
520

Current Day: 2014-12-29 00:00:00
15
520

Current Day: 2014-12-30 00:00:00
15
520

Current Day: 2014-12-31 00:00:00
15
520

Current Day: 2015-01-01 00:00:00
15
520

Current Day: 2015-01-02 00:00:00
15
520

Current Day: 2015-01-05 00:00:00
15
520
NET MONEY FROM LIQUIDATION: -228.75

Current Day: 2015-01-06 00:00:00
15
520

Current Day: 2015-01-07 00:00:00
15
520

Current Day: 2015-01-08 00:00:00
15
520

Current Day: 2015-01-09 00:00:00
15
520

Current Day: 2015-01-12 00:00:00
15
520

Current Day: 2015-01-13 00:00:00
15
520
NET MONEY FROM LIQUIDATION: -270.25

Current Day: 2015-01-14 00:00:00
15
520

Current Day: 2015-01-15 00:00:00
15
520

Current Day: 2015-01-16 00:00:00
15
520

Current Day: 2015-01-19 00:00:00
15
520

Current Day: 2015-01-20 00:00:00
15
520

Current Day: 2015-01-21 00:00:00
15
520

Current Day: 2015-01-22 00:00:00
15
520

Current Day: 2015-01-23 00:00:00
15
520

Current Day: 2015-01-26 00:00:00
15
520

Current Day: 2015-01-27 0

NET MONEY FROM LIQUIDATION: 726.75

Current Day: 2015-09-14 00:00:00
15
520

Current Day: 2015-09-15 00:00:00
15
520
NET MONEY FROM LIQUIDATION: 399.75

Current Day: 2015-09-16 00:00:00
15
520

Current Day: 2015-09-17 00:00:00
15
520

Current Day: 2015-09-18 00:00:00
15
520

Current Day: 2015-09-21 00:00:00
15
520

Current Day: 2015-09-22 00:00:00
15
520

Current Day: 2015-09-23 00:00:00
15
520

Current Day: 2015-09-24 00:00:00
15
520

Current Day: 2015-09-25 00:00:00
15
520

Current Day: 2015-09-28 00:00:00
15
520

Current Day: 2015-09-29 00:00:00
15
520

Current Day: 2015-09-30 00:00:00
15
520

Current Day: 2015-10-01 00:00:00
15
520

Current Day: 2015-10-02 00:00:00
15
520

Current Day: 2015-10-05 00:00:00
15
520

Current Day: 2015-10-06 00:00:00
15
520

Current Day: 2015-10-07 00:00:00
15
520

Current Day: 2015-10-08 00:00:00
15
520
NET MONEY FROM LIQUIDATION: -587.75

Current Day: 2015-10-09 00:00:00
15
520

Current Day: 2015-10-12 00:00:00
15
520

Current Day: 2015-10-13 00:00:00


Current Day: 2016-05-25 00:00:00
15
520

Current Day: 2016-05-26 00:00:00
15
520

Current Day: 2016-05-27 00:00:00
15
520

Current Day: 2016-05-30 00:00:00
15
520

Current Day: 2016-05-31 00:00:00
15
520

Current Day: 2016-06-01 00:00:00
15
520
NET MONEY FROM LIQUIDATION: 330.0

Current Day: 2016-06-02 00:00:00
15
520

Current Day: 2016-06-03 00:00:00
15
520

Current Day: 2016-06-06 00:00:00
15
520

Current Day: 2016-06-07 00:00:00
15
520

Current Day: 2016-06-08 00:00:00
15
520

Current Day: 2016-06-09 00:00:00
15
520

Current Day: 2016-06-10 00:00:00
15
520

Current Day: 2016-06-13 00:00:00
15
520

Current Day: 2016-06-14 00:00:00
15
520

Current Day: 2016-06-15 00:00:00
15
520

Current Day: 2016-06-16 00:00:00
15
520

Current Day: 2016-06-17 00:00:00
15
520
NET MONEY FROM LIQUIDATION: -308.5

Current Day: 2016-06-20 00:00:00
15
520

Current Day: 2016-06-21 00:00:00
15
520

Current Day: 2016-06-22 00:00:00
15
520
NET MONEY FROM LIQUIDATION: 184.5

Current Day: 2016-06-23 00:00:00
15

NET MONEY FROM LIQUIDATION: -42.75

Current Day: 2017-01-30 00:00:00
15
520

Current Day: 2017-01-31 00:00:00
15
520

Current Day: 2017-02-01 00:00:00
15
520
NET MONEY FROM LIQUIDATION: -82.25

Current Day: 2017-02-02 00:00:00
15
520

Current Day: 2017-02-03 00:00:00
15
520

Current Day: 2017-02-06 00:00:00
15
520

Current Day: 2017-02-07 00:00:00
15
520

Current Day: 2017-02-08 00:00:00
15
520

Current Day: 2017-02-09 00:00:00
15
520

Current Day: 2017-02-10 00:00:00
15
520

Current Day: 2017-02-13 00:00:00
15
520

Current Day: 2017-02-14 00:00:00
15
520

Current Day: 2017-02-15 00:00:00
15
520

Current Day: 2017-02-16 00:00:00
15
520

Current Day: 2017-02-17 00:00:00
15
520

Current Day: 2017-02-20 00:00:00
15
520

Current Day: 2017-02-21 00:00:00
15
520

Current Day: 2017-02-22 00:00:00
15
520

Current Day: 2017-02-23 00:00:00
15
520

Current Day: 2017-02-24 00:00:00
15
520
NET MONEY FROM LIQUIDATION: 282.5

Current Day: 2017-02-27 00:00:00
15
520

Current Day: 2017-02-28 00:00:00
1

In [28]:
%matplotlib qt

In [130]:
# Plot cumulative profit against general level

def plot_profit(strategies, name):

    fig, ax = plt.subplots(2,1)
    for i, st in enumerate(strategies):
        strat = strategies[st]
        TV_hist = strat.portfolio.total_value
        TV_hist = np.concatenate((np.full(strat.wdw_length, 100000), TV_hist))
        daily_dd, max_daily_dd = max_dd(TV_hist)
        ax[1].plot(strat.df.index[1:], TV_hist, label=st)
        daily_dd.plot(ax=ax[0], label=st)
        max_daily_dd.plot(ax=ax[0], label=st)
    
#     strat.df['level'].plot(ax=ax[1])
    ax[0].legend(loc='upper left')
    ax[1].legend(loc='upper left')
    ax[0].set_title("Daily and Max Drawdown")
    ax[1].set_title("Total Value of Portfolio")
    ax[0].set_ylabel("\$")
    ax[0].tick_params(
    axis='x',          # changes apply to the x-axis
    which='both',      # both major and minor ticks are affected
    bottom=False,      # ticks along the bottom edge are off
    top=False,         # ticks along the top edge are off
    labelbottom=False)
    plt.tight_layout()
    if savefig: plt.savefig("{}.pgf".format(name))

In [169]:
plot_profit(expanding_strats, 'expanding_strats')

In [39]:
def sharpe_ratio(returns):
    returns=np.array(returns)
    avg_return = returns.mean()
    std = returns.std()
    return avg_return*np.sqrt(252)/std

In [40]:
def max_dd(returns):
    
    window = 252
    
    returns = pd.Series(returns)
    roll_max = returns.rolling(window, min_periods=1).max()
    daily_dd = returns/roll_max - 1.0
    max_daily_dd = pd.Series(daily_dd).rolling(window, min_periods=1).min()
    return daily_dd, max_daily_dd
    

In [41]:
# Plot correlation coefficient between level and profit/return
def create_strat_table(strategies):
    from scipy.stats import spearmanr, pearsonr
    from tabulate import tabulate
    table = []
    for st in strategies:
        strat = strategies[st]
        capital = strat.portfolio.capital
        TV_hist = strat.portfolio.total_value
        TV_hist = np.concatenate((np.full(strat.wdw_length, 100000), TV_hist))
        returns = pd.Series(TV_hist).pct_change()
        mean = returns.mean()
        std = returns.std()
        sharpe = sharpe_ratio(returns.bfill())
        daily_dd, max_daily_dd = max_dd(TV_hist)
        dd=min(max_daily_dd)
        
        try:
            pearson = pearsonr(TV_hist, strat.df['level'].pct_change()[1:])
        except:
            pearson = pearsonr(TV_hist[1:], strat.df['level'].pct_change().dropna())
            
        table.append([st, capital, float('%.2g' % mean), float('%.2g' % std), float('%.2g' % sharpe), float('%.2g' % dd), float('%.2g' % pearson[0]), float('%.2g' % pearson[1])])
        
    headers = ["Strat", "Final capital", "mean", "Std", "sharpe", "dd", "Coefficient", "p-value"]
    print(tabulate(table, headers=headers, tablefmt='latex_raw'))

In [93]:
create_strat_table(expanding_strats)

\begin{tabular}{rrrrrrrr}
\hline
   Strat &   Final capital &    mean &     Std &   sharpe &     dd &   Coefficient &   p-value \\
\hline
       3 &          107989 & 4.1e-05 & 0.00084 &     0.77 & -0.026 &        -0.034 &      0.14 \\
       5 &          111600 & 5.8e-05 & 0.00076 &     1.2  & -0.016 &        -0.031 &      0.17 \\
      10 &          116948 & 8.3e-05 & 0.0013  &     1    & -0.02  &        -0.035 &      0.13 \\
      15 &          116317 & 8e-05   & 0.0013  &     1    & -0.024 &        -0.034 &      0.14 \\
\hline
\end{tabular}


In [94]:
create_strat_table(benchmark_strategies_exp)

\begin{tabular}{rrrrrrrr}
\hline
   Strat &   Final capital &    mean &     Std &   sharpe &     dd &   Coefficient &   p-value \\
\hline
       3 &          106677 & 3.4e-05 & 0.00088 &     0.62 & -0.025 &        -0.028 &     0.23  \\
       5 &          112487 & 6.2e-05 & 0.0009  &     1.1  & -0.012 &        -0.033 &     0.16  \\
      10 &          106158 & 3.2e-05 & 0.00092 &     0.55 & -0.023 &        -0.037 &     0.11  \\
      15 &          112043 & 6e-05   & 0.001   &     0.96 & -0.015 &        -0.039 &     0.092 \\
\hline
\end{tabular}


In [95]:
create_strat_table(strategies)

\begin{tabular}{lrrrrrrr}
\hline
 Strat   &   Final capital &    mean &     Std &   sharpe &      dd &   Coefficient &   p-value \\
\hline
 3-504   &          102584 & 1.4e-05 & 0.00059 &     0.37 & -0.021  &       0.003   &      0.89 \\
 5-504   &          104705 & 2.4e-05 & 0.00053 &     0.73 & -0.02   &      -0.014   &      0.54 \\
 10-504  &          104850 & 2.5e-05 & 0.00074 &     0.54 & -0.021  &      -0.03    &      0.2  \\
 15-504  &          103960 & 2.1e-05 & 0.0007  &     0.47 & -0.03   &       0.0067  &      0.77 \\
 3-756   &          104460 & 2.3e-05 & 0.0005  &     0.74 & -0.014  &      -0.02    &      0.38 \\
 5-756   &          103719 & 1.9e-05 & 0.00057 &     0.54 & -0.019  &      -0.012   &      0.6  \\
 10-756  &          102673 & 1.4e-05 & 0.00056 &     0.4  & -0.023  &      -0.0012  &      0.96 \\
 15-756  &          104640 & 2.4e-05 & 0.00062 &     0.61 & -0.02   &      -0.024   &      0.29 \\
 3-1008  &          103063 & 1.6e-05 & 0.00026 &     0.99 & -0.0037 &

In [96]:
create_strat_table(benchmark_strategies_fixed)

\begin{tabular}{lrrrrrrr}
\hline
 Strat   &   Final capital &    mean &     Std &   sharpe &      dd &   Coefficient &   p-value \\
\hline
 3-504   &          108545 & 4.4e-05 & 0.00097 &     0.72 & -0.021  &      -0.023   &      0.31 \\
 3-756   &          105100 & 2.6e-05 & 0.0005  &     0.83 & -0.02   &      -0.022   &      0.35 \\
 3-1008  &          104358 & 2.3e-05 & 0.00029 &     1.3  & -0.0043 &      -0.00084 &      0.97 \\
 5-504   &          108172 & 4.2e-05 & 0.00077 &     0.86 & -0.012  &      -0.032   &      0.17 \\
 5-756   &          109272 & 4.7e-05 & 0.00076 &     0.99 & -0.014  &      -0.027   &      0.24 \\
 5-1008  &          103532 & 1.8e-05 & 0.00025 &     1.1  & -0.0032 &      -0.0021  &      0.93 \\
 10-504  &          104499 & 2.3e-05 & 0.00055 &     0.67 & -0.012  &      -0.032   &      0.16 \\
 10-756  &          104871 & 2.5e-05 & 0.00061 &     0.66 & -0.011  &      -0.032   &      0.17 \\
 10-1008 &          103450 & 1.8e-05 & 0.00028 &     1    & -0.0033 &

In [102]:
%matplotlib qt
pd.DataFrame(benchmark_strategies_fixed['3-504'].portfolio.total_value).plot()

<AxesSubplot:>

In [105]:
max_dd(benchmark_strategies_fixed['3-504'].portfolio.total_value)

-0.020502867718301898

In [ ]:
print(returns)

In [36]:
benchmark_strategies_fixed

{'3-504': <__main__.PCA_Strategy at 0x146c57be0>,
 '3-756': <__main__.PCA_Strategy at 0x146c5dfa0>,
 '3-1008': <__main__.PCA_Strategy at 0x146c577c0>,
 '5-504': <__main__.PCA_Strategy at 0x146c5da90>,
 '5-756': <__main__.PCA_Strategy at 0x148d33310>,
 '5-1008': <__main__.PCA_Strategy at 0x1466b3850>,
 '10-504': <__main__.PCA_Strategy at 0x12a6d7520>,
 '10-756': <__main__.PCA_Strategy at 0x1466b3190>,
 '10-1008': <__main__.PCA_Strategy at 0x148d33370>,
 '15-504': <__main__.PCA_Strategy at 0x10cca7e80>,
 '15-756': <__main__.PCA_Strategy at 0x148cca520>,
 '15-1008': <__main__.PCA_Strategy at 0x1466aceb0>}

In [131]:
create_strat_table(expanding_strats)

NameError: name 'create_strat_table' is not defined

In [125]:
final_test_df_fixed = final_train_df.iloc[-1008:, :].append(final_test_df)

/var/folders/bn/nf5j5v796jjb6bncp9wnk5l80000gn/T/ipykernel_7486/3982586075.py:1: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_train_df.iloc[-1008:, :].append(final_test_df).iloc[1000:1010,:]


0        1       2        3        4       5        6  \
Date                                                                     
2017-04-06  360.75  368.500  376.25  386.000  395.000  401.00  406.000   
2017-04-07  359.50  367.250  374.75  384.500  393.500  399.50  404.500   
2017-04-10  367.00  374.500  381.75  391.000  399.500  405.00  410.000   
2017-04-11  366.50  373.750  380.75  390.500  399.250  405.00  410.000   
2017-04-12  369.00  376.000  382.75  392.500  401.000  406.75  411.500   
2017-04-13  371.00  378.000  384.50  394.500  403.500  409.25  413.750   
2017-04-14  368.75  375.625  382.25  392.375  401.625  407.25  411.625   
2017-04-17  366.50  373.250  380.00  390.250  399.750  405.25  409.500   
2017-04-18  361.75  368.250  375.75  386.250  396.000  402.00  406.750   
2017-04-19  361.75  368.250  375.75  386.500  396.250  401.75  406.500   

                  7        8       9    level  volatility      obs1      obs2  
Date                                                                           
2017-04-06  399.250  400.000  407.00  389.975    4.166541 -0.007634 -0.179934  
2017-04-07  399.250  401.250  408.00  389.200    3.828711 -0.001987 -0.337830  
2017-04-10  404.500  406.500  413.25  395.300    3.826283  0.015673 -0.002428  
2017-04-11  404.250  406.250  413.00  394.925    3.715098 -0.000949 -0.111186  
2017-04-12  405.750  407.000  414.00  396.625    3.586766  0.004305 -0.128332  
2017-04-13  407.250  407.750  414.50  398.400    2.974719  0.004475 -0.612047  
2017-04-14  404.875  405.625  412.50  396.250    3.037919 -0.005397  0.063200  
2017-04-17  402.500  403.500  410.50  394.100    3.006655 -0.005426 -0.031264  
2017-04-18  400.250  401.250  408.25  390.650    3.075467       NaN       NaN  
2017-04-19  400.000  401.000  408.00  390.575    3.239727       NaN       NaN

In [33]:
test_strategies = dict()
for wdw_length, holding_period in [(1008, 5), (1008, 15), (1008, 3)]:
    final_test_df_fixed = final_train_df.iloc[-1*wdw_length:, :].append(final_test_df)
    strategy = PCA_HMM_Strategy(final_test_df_fixed, 3, 15, 100000, False)
    strategy.__run__(holding_period, wdw_length, wdw_length)
    if not strategy.portfolio.__is_empty__():
        strategy.portfolio.__liquidate__(strategy.curr_day, strategy.df)

    test_strategies[str(holding_period) + "-"  + str(wdw_length)] = strategy

/var/folders/bn/nf5j5v796jjb6bncp9wnk5l80000gn/T/ipykernel_957/4113497346.py:3: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_test_df_fixed = final_train_df.iloc[-1*wdw_length:, :].append(final_test_df)



Current Day: 2017-04-18 00:00:00
5
1008

Current Day: 2017-04-19 00:00:00
5
1008

Current Day: 2017-04-20 00:00:00
5
1008

Current Day: 2017-04-21 00:00:00
5
1008

Current Day: 2017-04-24 00:00:00
5
1008

Current Day: 2017-04-25 00:00:00
5
1008

Current Day: 2017-04-26 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 33.5

Current Day: 2017-04-27 00:00:00
5
1008

Current Day: 2017-04-28 00:00:00
5
1008

Current Day: 2017-05-01 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 553.5

Current Day: 2017-05-02 00:00:00
5
1008

Current Day: 2017-05-03 00:00:00
5
1008

Current Day: 2017-05-04 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 121.0

Current Day: 2017-05-05 00:00:00
5
1008

Current Day: 2017-05-08 00:00:00
5
1008

Current Day: 2017-05-09 00:00:00
5
1008

Current Day: 2017-05-10 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: -706.25

Current Day: 2017-05-11 00:00:00
5
1008

Current Day: 2017-05-12 00:00:00
5
1008

Current Day: 2017-05-15 00:00:00
5
1008

Current Day: 2017-05-16 00:00:00
5
1008

C

NET MONEY FROM LIQUIDATION: -365.3392857142858

Current Day: 2017-12-15 00:00:00
5
1008

Current Day: 2017-12-18 00:00:00
5
1008

Current Day: 2017-12-19 00:00:00
5
1008

Current Day: 2017-12-20 00:00:00
5
1008

Current Day: 2017-12-21 00:00:00
5
1008

Current Day: 2017-12-22 00:00:00
5
1008

Current Day: 2017-12-25 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 583.6373626373643

Current Day: 2017-12-26 00:00:00
5
1008

Current Day: 2017-12-27 00:00:00
5
1008

Current Day: 2017-12-28 00:00:00
5
1008

Current Day: 2017-12-29 00:00:00
5
1008

Current Day: 2018-01-01 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 23.64560439560455

Current Day: 2018-01-02 00:00:00
5
1008

Current Day: 2018-01-03 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: -219.5

Current Day: 2018-01-04 00:00:00
5
1008

Current Day: 2018-01-05 00:00:00
5
1008

Current Day: 2018-01-08 00:00:00
5
1008

Current Day: 2018-01-09 00:00:00
5
1008

Current Day: 2018-01-10 00:00:00
5
1008

Current Day: 2018-01-11 00:00:00
5
1008

Curre


Current Day: 2018-08-10 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 339.25

Current Day: 2018-08-13 00:00:00
5
1008

Current Day: 2018-08-14 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 982.25

Current Day: 2018-08-15 00:00:00
5
1008

Current Day: 2018-08-16 00:00:00
5
1008

Current Day: 2018-08-17 00:00:00
5
1008

Current Day: 2018-08-20 00:00:00
5
1008

Current Day: 2018-08-21 00:00:00
5
1008

Current Day: 2018-08-22 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 636.75

Current Day: 2018-08-23 00:00:00
5
1008

Current Day: 2018-08-24 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 116.5

Current Day: 2018-08-27 00:00:00
5
1008

Current Day: 2018-08-28 00:00:00
5
1008

Current Day: 2018-08-29 00:00:00
5
1008

Current Day: 2018-08-30 00:00:00
5
1008

Current Day: 2018-08-31 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: -172.25

Current Day: 2018-09-03 00:00:00
5
1008

Current Day: 2018-09-04 00:00:00
5
1008

Current Day: 2018-09-05 00:00:00
5
1008

Current Day: 2018-09-06 00:00:00
5
1008

Curr


Current Day: 2019-04-05 00:00:00
5
1008

Current Day: 2019-04-08 00:00:00
5
1008

Current Day: 2019-04-09 00:00:00
5
1008

Current Day: 2019-04-10 00:00:00
5
1008

Current Day: 2019-04-11 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 1159.5

Current Day: 2019-04-12 00:00:00
5
1008

Current Day: 2019-04-15 00:00:00
5
1008

Current Day: 2019-04-16 00:00:00
5
1008

Current Day: 2019-04-17 00:00:00
5
1008

Current Day: 2019-04-18 00:00:00
5
1008

Current Day: 2019-04-19 00:00:00
5
1008

Current Day: 2019-04-22 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 780.5

Current Day: 2019-04-23 00:00:00
5
1008

Current Day: 2019-04-24 00:00:00
5
1008

Current Day: 2019-04-25 00:00:00
5
1008

Current Day: 2019-04-26 00:00:00
5
1008

Current Day: 2019-04-29 00:00:00
5
1008

Current Day: 2019-04-30 00:00:00
5
1008

Current Day: 2019-05-01 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 65.0

Current Day: 2019-05-02 00:00:00
5
1008

Current Day: 2019-05-03 00:00:00
5
1008

Current Day: 2019-05-06 00:00:00
5
1

...


Current Day: 2019-03-14 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: -168.25

Current Day: 2019-03-15 00:00:00
3
1008

Current Day: 2019-03-18 00:00:00
3
1008

Current Day: 2019-03-19 00:00:00
3
1008

Current Day: 2019-03-20 00:00:00
3
1008

Current Day: 2019-03-21 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: -256.5

Current Day: 2019-03-22 00:00:00
3
1008

Current Day: 2019-03-25 00:00:00
3
1008

Current Day: 2019-03-26 00:00:00
3
1008

Current Day: 2019-03-27 00:00:00
3
1008

Current Day: 2019-03-28 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: 485.0

Current Day: 2019-03-29 00:00:00
3
1008

Current Day: 2019-04-01 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: 233.5

Current Day: 2019-04-02 00:00:00
3
1008

Current Day: 2019-04-03 00:00:00
3
1008

Current Day: 2019-04-04 00:00:00
3
1008

Current Day: 2019-04-05 00:00:00
3
1008

Current Day: 2019-04-08 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: 2273.25

Current Day: 2019-04-09 00:00:00
3
1008

Current Day: 2019-04-10 00:00:00
3
1008

Curr


Current Day: 2019-10-25 00:00:00
3
1008

Current Day: 2019-10-28 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: -548.0

Current Day: 2019-10-29 00:00:00
3
1008

Current Day: 2019-10-30 00:00:00
3
1008

Current Day: 2019-10-31 00:00:00
3
1008

Current Day: 2019-11-01 00:00:00
3
1008

Current Day: 2019-11-04 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: -490.75

Current Day: 2019-11-05 00:00:00
3
1008

Current Day: 2019-11-06 00:00:00
3
1008

Current Day: 2019-11-07 00:00:00
3
1008

Current Day: 2019-11-08 00:00:00
3
1008

Current Day: 2019-11-11 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: 393.75

Current Day: 2019-11-12 00:00:00
3
1008

Current Day: 2019-11-13 00:00:00
3
1008

Current Day: 2019-11-14 00:00:00
3
1008

Current Day: 2019-11-15 00:00:00
3
1008

Current Day: 2019-11-18 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: 34.75

Current Day: 2019-11-19 00:00:00
3
1008

Current Day: 2019-11-20 00:00:00
3
1008

Current Day: 2019-11-21 00:00:00
3
1008

Current Day: 2019-11-22 00:00:00
3
1008


Current Day: 2020-06-15 00:00:00
3
1008

Current Day: 2020-06-16 00:00:00
3
1008

Current Day: 2020-06-17 00:00:00
3
1008

Current Day: 2020-06-18 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: 338.75

Current Day: 2020-06-19 00:00:00
3
1008

Current Day: 2020-06-22 00:00:00
3
1008

Current Day: 2020-06-23 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: -27.25

Current Day: 2020-06-24 00:00:00
3
1008

Current Day: 2020-06-25 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: -80.5

Current Day: 2020-06-26 00:00:00
3
1008

Current Day: 2020-06-29 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: -23.25

Current Day: 2020-06-30 00:00:00
3
1008

Current Day: 2020-07-01 00:00:00
3
1008

Current Day: 2020-07-02 00:00:00
3
1008

Current Day: 2020-07-03 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: -664.25

Current Day: 2020-07-06 00:00:00
3
1008

Current Day: 2020-07-07 00:00:00
3
1008

Current Day: 2020-07-08 00:00:00
3
1008

Current Day: 2020-07-09 00:00:00
3
1008

Current Day: 2020-07-10 00:00:00
3
1008
NET M

NET MONEY FROM LIQUIDATION: -871.0

Current Day: 2021-01-28 00:00:00
3
1008

Current Day: 2021-01-29 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: 161.75

Current Day: 2021-02-01 00:00:00
3
1008

Current Day: 2021-02-02 00:00:00
3
1008

Current Day: 2021-02-03 00:00:00
3
1008

Current Day: 2021-02-04 00:00:00
3
1008

Current Day: 2021-02-05 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: -758.0

Current Day: 2021-02-08 00:00:00
3
1008

Current Day: 2021-02-09 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: -284.0

Current Day: 2021-02-10 00:00:00
3
1008

Current Day: 2021-02-11 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: -1168.25

Current Day: 2021-02-12 00:00:00
3
1008

Current Day: 2021-02-15 00:00:00
3
1008

Current Day: 2021-02-16 00:00:00
3
1008

Current Day: 2021-02-17 00:00:00
3
1008

Current Day: 2021-02-18 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: -972.75

Current Day: 2021-02-19 00:00:00
3
1008

Current Day: 2021-02-22 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: -356.25

Current Day:

NET MONEY FROM LIQUIDATION: 352.0

Current Day: 2021-09-03 00:00:00
3
1008

Current Day: 2021-09-06 00:00:00
3
1008

Current Day: 2021-09-07 00:00:00
3
1008

Current Day: 2021-09-08 00:00:00
3
1008

Current Day: 2021-09-09 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: -6.5

Current Day: 2021-09-10 00:00:00
3
1008

Current Day: 2021-09-13 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: 675.0

Current Day: 2021-09-14 00:00:00
3
1008

Current Day: 2021-09-15 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: 277.5

Current Day: 2021-09-16 00:00:00
3
1008

Current Day: 2021-09-17 00:00:00
3
1008

Current Day: 2021-09-20 00:00:00
3
1008

Current Day: 2021-09-21 00:00:00
3
1008

Current Day: 2021-09-22 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: 626.0

Current Day: 2021-09-23 00:00:00
3
1008

Current Day: 2021-09-24 00:00:00
3
1008

Current Day: 2021-09-27 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: -65.75

Current Day: 2021-09-28 00:00:00
3
1008

Current Day: 2021-09-29 00:00:00
3
1008

Current Day: 202

In [34]:
benchmark_test_strategies = dict()
for wdw_length, holding_period in [(1008, 5), (1008, 15), (1008, 3)]:
    final_test_df_fixed = final_train_df.iloc[-1*wdw_length:, :].append(final_test_df)
    strategy = PCA_Strategy(final_test_df_fixed, 15, 100000, False)
    strategy.__run__(holding_period, wdw_length, wdw_length)
    if not strategy.portfolio.__is_empty__():
        strategy.portfolio.__liquidate__(strategy.curr_day, strategy.df)

    benchmark_test_strategies[str(holding_period) + "-"  + str(wdw_length)] = strategy


Current Day: 2017-04-18 00:00:00
5
1008


/var/folders/bn/nf5j5v796jjb6bncp9wnk5l80000gn/T/ipykernel_957/1725083089.py:3: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_test_df_fixed = final_train_df.iloc[-1*wdw_length:, :].append(final_test_df)



Current Day: 2017-04-19 00:00:00
5
1008

Current Day: 2017-04-20 00:00:00
5
1008

Current Day: 2017-04-21 00:00:00
5
1008

Current Day: 2017-04-24 00:00:00
5
1008

Current Day: 2017-04-25 00:00:00
5
1008

Current Day: 2017-04-26 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 30.25

Current Day: 2017-04-27 00:00:00
5
1008

Current Day: 2017-04-28 00:00:00
5
1008

Current Day: 2017-05-01 00:00:00
5
1008

Current Day: 2017-05-02 00:00:00
5
1008

Current Day: 2017-05-03 00:00:00
5
1008

Current Day: 2017-05-04 00:00:00
5
1008

Current Day: 2017-05-05 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 355.5

Current Day: 2017-05-08 00:00:00
5
1008

Current Day: 2017-05-09 00:00:00
5
1008

Current Day: 2017-05-10 00:00:00
5
1008

Current Day: 2017-05-11 00:00:00
5
1008

Current Day: 2017-05-12 00:00:00
5
1008

Current Day: 2017-05-15 00:00:00
5
1008

Current Day: 2017-05-16 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 595.25

Current Day: 2017-05-17 00:00:00
5
1008

Current Day: 2017-05-18 00:00:00
5


NET MONEY FROM LIQUIDATION: 611.277472527474

Current Day: 2017-12-27 00:00:00
5
1008

Current Day: 2017-12-28 00:00:00
5
1008

Current Day: 2017-12-29 00:00:00
5
1008

Current Day: 2018-01-01 00:00:00
5
1008

Current Day: 2018-01-02 00:00:00
5
1008

Current Day: 2018-01-03 00:00:00
5
1008

Current Day: 2018-01-04 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 86.25

Current Day: 2018-01-05 00:00:00
5
1008

Current Day: 2018-01-08 00:00:00
5
1008

Current Day: 2018-01-09 00:00:00
5
1008

Current Day: 2018-01-10 00:00:00
5
1008

Current Day: 2018-01-11 00:00:00
5
1008

Current Day: 2018-01-12 00:00:00
5
1008

Current Day: 2018-01-15 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 265.875

Current Day: 2018-01-16 00:00:00
5
1008

Current Day: 2018-01-17 00:00:00
5
1008

Current Day: 2018-01-18 00:00:00
5
1008

Current Day: 2018-01-19 00:00:00
5
1008

Current Day: 2018-01-22 00:00:00
5
1008

Current Day: 2018-01-23 00:00:00
5
1008

Current Day: 2018-01-24 00:00:00
5
1008
NET MONEY FROM LIQUIDATI


Current Day: 2018-09-04 00:00:00
5
1008

Current Day: 2018-09-05 00:00:00
5
1008

Current Day: 2018-09-06 00:00:00
5
1008

Current Day: 2018-09-07 00:00:00
5
1008

Current Day: 2018-09-10 00:00:00
5
1008

Current Day: 2018-09-11 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 232.0

Current Day: 2018-09-12 00:00:00
5
1008

Current Day: 2018-09-13 00:00:00
5
1008

Current Day: 2018-09-14 00:00:00
5
1008

Current Day: 2018-09-17 00:00:00
5
1008

Current Day: 2018-09-18 00:00:00
5
1008

Current Day: 2018-09-19 00:00:00
5
1008

Current Day: 2018-09-20 00:00:00
5
1008

Current Day: 2018-09-21 00:00:00
5
1008

Current Day: 2018-09-24 00:00:00
5
1008

Current Day: 2018-09-25 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: -344.0

Current Day: 2018-09-26 00:00:00
5
1008

Current Day: 2018-09-27 00:00:00
5
1008

Current Day: 2018-09-28 00:00:00
5
1008

Current Day: 2018-10-01 00:00:00
5
1008

Current Day: 2018-10-02 00:00:00
5
1008

Current Day: 2018-10-03 00:00:00
5
1008

Current Day: 2018-10-04 00:0

...


Current Day: 2019-04-09 00:00:00
3
1008

Current Day: 2019-04-10 00:00:00
3
1008

Current Day: 2019-04-11 00:00:00
3
1008

Current Day: 2019-04-12 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: 150.25

Current Day: 2019-04-15 00:00:00
3
1008

Current Day: 2019-04-16 00:00:00
3
1008

Current Day: 2019-04-17 00:00:00
3
1008

Current Day: 2019-04-18 00:00:00
3
1008

Current Day: 2019-04-19 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: 483.375

Current Day: 2019-04-22 00:00:00
3
1008

Current Day: 2019-04-23 00:00:00
3
1008

Current Day: 2019-04-24 00:00:00
3
1008

Current Day: 2019-04-25 00:00:00
3
1008

Current Day: 2019-04-26 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: 708.75

Current Day: 2019-04-29 00:00:00
3
1008

Current Day: 2019-04-30 00:00:00
3
1008

Current Day: 2019-05-01 00:00:00
3
1008

Current Day: 2019-05-02 00:00:00
3
1008

Current Day: 2019-05-03 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: 1424.0

Current Day: 2019-05-06 00:00:00
3
1008

Current Day: 2019-05-07 00:00:00
3
100


Current Day: 2019-12-06 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: -512.0

Current Day: 2019-12-09 00:00:00
3
1008

Current Day: 2019-12-10 00:00:00
3
1008

Current Day: 2019-12-11 00:00:00
3
1008

Current Day: 2019-12-12 00:00:00
3
1008

Current Day: 2019-12-13 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: -294.5

Current Day: 2019-12-16 00:00:00
3
1008

Current Day: 2019-12-17 00:00:00
3
1008

Current Day: 2019-12-18 00:00:00
3
1008

Current Day: 2019-12-19 00:00:00
3
1008

Current Day: 2019-12-20 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: -268.5178571428569

Current Day: 2019-12-23 00:00:00
3
1008

Current Day: 2019-12-24 00:00:00
3
1008

Current Day: 2019-12-25 00:00:00
3
1008

Current Day: 2019-12-26 00:00:00
3
1008

Current Day: 2019-12-27 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: -102.00000000000045

Current Day: 2019-12-30 00:00:00
3
1008

Current Day: 2019-12-31 00:00:00
3
1008

Current Day: 2020-01-01 00:00:00
3
1008

Current Day: 2020-01-02 00:00:00
3
1008

Current Day: 2


Current Day: 2020-08-03 00:00:00
3
1008

Current Day: 2020-08-04 00:00:00
3
1008

Current Day: 2020-08-05 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: 243.5

Current Day: 2020-08-06 00:00:00
3
1008

Current Day: 2020-08-07 00:00:00
3
1008

Current Day: 2020-08-10 00:00:00
3
1008

Current Day: 2020-08-11 00:00:00
3
1008

Current Day: 2020-08-12 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: 1201.75

Current Day: 2020-08-13 00:00:00
3
1008

Current Day: 2020-08-14 00:00:00
3
1008

Current Day: 2020-08-17 00:00:00
3
1008

Current Day: 2020-08-18 00:00:00
3
1008

Current Day: 2020-08-19 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: -62.75

Current Day: 2020-08-20 00:00:00
3
1008

Current Day: 2020-08-21 00:00:00
3
1008

Current Day: 2020-08-24 00:00:00
3
1008

Current Day: 2020-08-25 00:00:00
3
1008

Current Day: 2020-08-26 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: 159.0

Current Day: 2020-08-27 00:00:00
3
1008

Current Day: 2020-08-28 00:00:00
3
1008

Current Day: 2020-08-31 00:00:00
3
1008



Current Day: 2021-03-29 00:00:00
3
1008

Current Day: 2021-03-30 00:00:00
3
1008

Current Day: 2021-03-31 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: -1094.25

Current Day: 2021-04-01 00:00:00
3
1008

Current Day: 2021-04-02 00:00:00
3
1008

Current Day: 2021-04-05 00:00:00
3
1008

Current Day: 2021-04-06 00:00:00
3
1008

Current Day: 2021-04-07 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: 7.75

Current Day: 2021-04-08 00:00:00
3
1008

Current Day: 2021-04-09 00:00:00
3
1008

Current Day: 2021-04-12 00:00:00
3
1008

Current Day: 2021-04-13 00:00:00
3
1008

Current Day: 2021-04-14 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: -350.25

Current Day: 2021-04-15 00:00:00
3
1008

Current Day: 2021-04-16 00:00:00
3
1008

Current Day: 2021-04-19 00:00:00
3
1008

Current Day: 2021-04-20 00:00:00
3
1008

Current Day: 2021-04-21 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: -454.75

Current Day: 2021-04-22 00:00:00
3
1008

Current Day: 2021-04-23 00:00:00
3
1008

Current Day: 2021-04-26 00:00:00
3
10


Current Day: 2021-11-24 00:00:00
3
1008

Current Day: 2021-11-25 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: 467.5

Current Day: 2021-11-26 00:00:00
3
1008

Current Day: 2021-11-29 00:00:00
3
1008

Current Day: 2021-11-30 00:00:00
3
1008

Current Day: 2021-12-01 00:00:00
3
1008

Current Day: 2021-12-02 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: -872.75

Current Day: 2021-12-03 00:00:00
3
1008

Current Day: 2021-12-06 00:00:00
3
1008

Current Day: 2021-12-07 00:00:00
3
1008

Current Day: 2021-12-08 00:00:00
3
1008

Current Day: 2021-12-09 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: -152.25

Current Day: 2021-12-10 00:00:00
3
1008

Current Day: 2021-12-13 00:00:00
3
1008

Current Day: 2021-12-14 00:00:00
3
1008

Current Day: 2021-12-15 00:00:00
3
1008

Current Day: 2021-12-16 00:00:00
3
1008
NET MONEY FROM LIQUIDATION: 529.2928571428574

Current Day: 2021-12-17 00:00:00
3
1008

Current Day: 2021-12-20 00:00:00
3
1008

Current Day: 2021-12-21 00:00:00
3
1008

Current Day: 2021-12-22 00:

In [35]:
benchmark_test_strategies_exp = dict()
for holding_period in [5]:
    final_test_df_fixed = final_train_df.iloc[-1*wdw_length:, :].append(final_test_df)
    strategy = PCA_Strategy(final_test_df_fixed, 15, 100000, True)
    strategy.__run__(holding_period, 1008, 1008)
    if not strategy.portfolio.__is_empty__():
        strategy.portfolio.__liquidate__(strategy.curr_day, strategy.df)

    benchmark_test_strategies_exp[str(holding_period)] = strategy


Current Day: 2017-04-18 00:00:00
5
1008


/var/folders/bn/nf5j5v796jjb6bncp9wnk5l80000gn/T/ipykernel_957/3234577719.py:3: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_test_df_fixed = final_train_df.iloc[-1*wdw_length:, :].append(final_test_df)



Current Day: 2017-04-19 00:00:00
5
1008

Current Day: 2017-04-20 00:00:00
5
1008

Current Day: 2017-04-21 00:00:00
5
1008

Current Day: 2017-04-24 00:00:00
5
1008

Current Day: 2017-04-25 00:00:00
5
1008

Current Day: 2017-04-26 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 30.25

Current Day: 2017-04-27 00:00:00
5
1008

Current Day: 2017-04-28 00:00:00
5
1008

Current Day: 2017-05-01 00:00:00
5
1008

Current Day: 2017-05-02 00:00:00
5
1008

Current Day: 2017-05-03 00:00:00
5
1008

Current Day: 2017-05-04 00:00:00
5
1008

Current Day: 2017-05-05 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 355.5

Current Day: 2017-05-08 00:00:00
5
1008

Current Day: 2017-05-09 00:00:00
5
1008

Current Day: 2017-05-10 00:00:00
5
1008

Current Day: 2017-05-11 00:00:00
5
1008

Current Day: 2017-05-12 00:00:00
5
1008

Current Day: 2017-05-15 00:00:00
5
1008

Current Day: 2017-05-16 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 232.75

Current Day: 2017-05-17 00:00:00
5
1008

Current Day: 2017-05-18 00:00:00
5


NET MONEY FROM LIQUIDATION: 239.2046703296703

Current Day: 2017-12-27 00:00:00
5
1008

Current Day: 2017-12-28 00:00:00
5
1008

Current Day: 2017-12-29 00:00:00
5
1008

Current Day: 2018-01-01 00:00:00
5
1008

Current Day: 2018-01-02 00:00:00
5
1008

Current Day: 2018-01-03 00:00:00
5
1008

Current Day: 2018-01-04 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 1002.5

Current Day: 2018-01-05 00:00:00
5
1008

Current Day: 2018-01-08 00:00:00
5
1008

Current Day: 2018-01-09 00:00:00
5
1008

Current Day: 2018-01-10 00:00:00
5
1008

Current Day: 2018-01-11 00:00:00
5
1008

Current Day: 2018-01-12 00:00:00
5
1008

Current Day: 2018-01-15 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 307.625

Current Day: 2018-01-16 00:00:00
5
1008

Current Day: 2018-01-17 00:00:00
5
1008

Current Day: 2018-01-18 00:00:00
5
1008

Current Day: 2018-01-19 00:00:00
5
1008

Current Day: 2018-01-22 00:00:00
5
1008

Current Day: 2018-01-23 00:00:00
5
1008

Current Day: 2018-01-24 00:00:00
5
1008
NET MONEY FROM LIQUIDA


Current Day: 2018-09-04 00:00:00
5
1008

Current Day: 2018-09-05 00:00:00
5
1008

Current Day: 2018-09-06 00:00:00
5
1008

Current Day: 2018-09-07 00:00:00
5
1008

Current Day: 2018-09-10 00:00:00
5
1008

Current Day: 2018-09-11 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 55.75

Current Day: 2018-09-12 00:00:00
5
1008

Current Day: 2018-09-13 00:00:00
5
1008

Current Day: 2018-09-14 00:00:00
5
1008

Current Day: 2018-09-17 00:00:00
5
1008

Current Day: 2018-09-18 00:00:00
5
1008

Current Day: 2018-09-19 00:00:00
5
1008

Current Day: 2018-09-20 00:00:00
5
1008

Current Day: 2018-09-21 00:00:00
5
1008

Current Day: 2018-09-24 00:00:00
5
1008

Current Day: 2018-09-25 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: -736.0

Current Day: 2018-09-26 00:00:00
5
1008

Current Day: 2018-09-27 00:00:00
5
1008

Current Day: 2018-09-28 00:00:00
5
1008

Current Day: 2018-10-01 00:00:00
5
1008

Current Day: 2018-10-02 00:00:00
5
1008

Current Day: 2018-10-03 00:00:00
5
1008

Current Day: 2018-10-04 00:0


Current Day: 2019-05-14 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 236.5

Current Day: 2019-05-15 00:00:00
5
1008

Current Day: 2019-05-16 00:00:00
5
1008

Current Day: 2019-05-17 00:00:00
5
1008

Current Day: 2019-05-20 00:00:00
5
1008

Current Day: 2019-05-21 00:00:00
5
1008

Current Day: 2019-05-22 00:00:00
5
1008

Current Day: 2019-05-23 00:00:00
5
1008

Current Day: 2019-05-24 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 73.75

Current Day: 2019-05-27 00:00:00
5
1008

Current Day: 2019-05-28 00:00:00
5
1008

Current Day: 2019-05-29 00:00:00
5
1008

Current Day: 2019-05-30 00:00:00
5
1008

Current Day: 2019-05-31 00:00:00
5
1008

Current Day: 2019-06-03 00:00:00
5
1008

Current Day: 2019-06-04 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 436.0

Current Day: 2019-06-05 00:00:00
5
1008

Current Day: 2019-06-06 00:00:00
5
1008

Current Day: 2019-06-07 00:00:00
5
1008

Current Day: 2019-06-10 00:00:00
5
1008

Current Day: 2019-06-11 00:00:00
5
1008

Current Day: 2019-06-12 00:00:00
5
1


Current Day: 2020-01-20 00:00:00
5
1008

Current Day: 2020-01-21 00:00:00
5
1008

Current Day: 2020-01-22 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 323.25

Current Day: 2020-01-23 00:00:00
5
1008

Current Day: 2020-01-24 00:00:00
5
1008

Current Day: 2020-01-27 00:00:00
5
1008

Current Day: 2020-01-28 00:00:00
5
1008

Current Day: 2020-01-29 00:00:00
5
1008

Current Day: 2020-01-30 00:00:00
5
1008

Current Day: 2020-01-31 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: -71.25

Current Day: 2020-02-03 00:00:00
5
1008

Current Day: 2020-02-04 00:00:00
5
1008

Current Day: 2020-02-05 00:00:00
5
1008

Current Day: 2020-02-06 00:00:00
5
1008

Current Day: 2020-02-07 00:00:00
5
1008

Current Day: 2020-02-10 00:00:00
5
1008

Current Day: 2020-02-11 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 339.0

Current Day: 2020-02-12 00:00:00
5
1008

Current Day: 2020-02-13 00:00:00
5
1008

Current Day: 2020-02-14 00:00:00
5
1008

Current Day: 2020-02-17 00:00:00
5
1008

Current Day: 2020-02-18 00:00:00
5


Current Day: 2020-09-28 00:00:00
5
1008

Current Day: 2020-09-29 00:00:00
5
1008

Current Day: 2020-09-30 00:00:00
5
1008

Current Day: 2020-10-01 00:00:00
5
1008

Current Day: 2020-10-02 00:00:00
5
1008

Current Day: 2020-10-05 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: -1114.5

Current Day: 2020-10-06 00:00:00
5
1008

Current Day: 2020-10-07 00:00:00
5
1008

Current Day: 2020-10-08 00:00:00
5
1008

Current Day: 2020-10-09 00:00:00
5
1008

Current Day: 2020-10-12 00:00:00
5
1008

Current Day: 2020-10-13 00:00:00
5
1008

Current Day: 2020-10-14 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 331.0

Current Day: 2020-10-15 00:00:00
5
1008

Current Day: 2020-10-16 00:00:00
5
1008

Current Day: 2020-10-19 00:00:00
5
1008

Current Day: 2020-10-20 00:00:00
5
1008

Current Day: 2020-10-21 00:00:00
5
1008

Current Day: 2020-10-22 00:00:00
5
1008

Current Day: 2020-10-23 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 464.25

Current Day: 2020-10-26 00:00:00
5
1008

Current Day: 2020-10-27 00:00:00



Current Day: 2021-06-07 00:00:00
5
1008

Current Day: 2021-06-08 00:00:00
5
1008

Current Day: 2021-06-09 00:00:00
5
1008

Current Day: 2021-06-10 00:00:00
5
1008

Current Day: 2021-06-11 00:00:00
5
1008

Current Day: 2021-06-14 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 354.5

Current Day: 2021-06-15 00:00:00
5
1008

Current Day: 2021-06-16 00:00:00
5
1008

Current Day: 2021-06-17 00:00:00
5
1008

Current Day: 2021-06-18 00:00:00
5
1008

Current Day: 2021-06-21 00:00:00
5
1008

Current Day: 2021-06-22 00:00:00
5
1008

Current Day: 2021-06-23 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 147.75

Current Day: 2021-06-24 00:00:00
5
1008

Current Day: 2021-06-25 00:00:00
5
1008

Current Day: 2021-06-28 00:00:00
5
1008

Current Day: 2021-06-29 00:00:00
5
1008

Current Day: 2021-06-30 00:00:00
5
1008

Current Day: 2021-07-01 00:00:00
5
1008

Current Day: 2021-07-02 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 581.25

Current Day: 2021-07-05 00:00:00
5
1008

Current Day: 2021-07-06 00:00:00
5

NET MONEY FROM LIQUIDATION: 1111.5

Current Day: 2022-02-14 00:00:00
5
1008

Current Day: 2022-02-15 00:00:00
5
1008

Current Day: 2022-02-16 00:00:00
5
1008

Current Day: 2022-02-17 00:00:00
5
1008

Current Day: 2022-02-18 00:00:00
5
1008

Current Day: 2022-02-21 00:00:00
5
1008

Current Day: 2022-02-22 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 473.75

Current Day: 2022-02-23 00:00:00
5
1008

Current Day: 2022-02-24 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 212.75


In [37]:
test_strategies_exp = dict()
for holding_period in [5]:
    final_test_df_fixed = final_train_df.iloc[-1*wdw_length:, :].append(final_test_df)
    strategy = PCA_HMM_Strategy(final_test_df_fixed, 3, 15, 100000, True)
    strategy.__run__(holding_period, 1008, 1008)
    if not strategy.portfolio.__is_empty__():
        strategy.portfolio.__liquidate__(strategy.curr_day, strategy.df)

    test_strategies_exp[str(holding_period)] = strategy

/var/folders/bn/nf5j5v796jjb6bncp9wnk5l80000gn/T/ipykernel_957/1813472794.py:3: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_test_df_fixed = final_train_df.iloc[-1*wdw_length:, :].append(final_test_df)



Current Day: 2017-04-18 00:00:00
5
1008

Current Day: 2017-04-19 00:00:00
5
1008

Current Day: 2017-04-20 00:00:00
5
1008

Current Day: 2017-04-21 00:00:00
5
1008

Current Day: 2017-04-24 00:00:00
5
1008

Current Day: 2017-04-25 00:00:00
5
1008

Current Day: 2017-04-26 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 33.5

Current Day: 2017-04-27 00:00:00
5
1008

Current Day: 2017-04-28 00:00:00
5
1008

Current Day: 2017-05-01 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 143.0

Current Day: 2017-05-02 00:00:00
5
1008

Current Day: 2017-05-03 00:00:00
5
1008

Current Day: 2017-05-04 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 105.0

Current Day: 2017-05-05 00:00:00
5
1008

Current Day: 2017-05-08 00:00:00
5
1008

Current Day: 2017-05-09 00:00:00
5
1008

Current Day: 2017-05-10 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 505.75

Current Day: 2017-05-11 00:00:00
5
1008

Current Day: 2017-05-12 00:00:00
5
1008

Current Day: 2017-05-15 00:00:00
5
1008

Current Day: 2017-05-16 00:00:00
5
1008

Cu

NET MONEY FROM LIQUIDATION: 74.87500000000023

Current Day: 2017-12-15 00:00:00
5
1008

Current Day: 2017-12-18 00:00:00
5
1008

Current Day: 2017-12-19 00:00:00
5
1008

Current Day: 2017-12-20 00:00:00
5
1008

Current Day: 2017-12-21 00:00:00
5
1008

Current Day: 2017-12-22 00:00:00
5
1008

Current Day: 2017-12-25 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 216.3640109890107

Current Day: 2017-12-26 00:00:00
5
1008

Current Day: 2017-12-27 00:00:00
5
1008

Current Day: 2017-12-28 00:00:00
5
1008

Current Day: 2017-12-29 00:00:00
5
1008

Current Day: 2018-01-01 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 869.2335164835167

Current Day: 2018-01-02 00:00:00
5
1008

Current Day: 2018-01-03 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: -678.0

Current Day: 2018-01-04 00:00:00
5
1008

Current Day: 2018-01-05 00:00:00
5
1008

Current Day: 2018-01-08 00:00:00
5
1008

Current Day: 2018-01-09 00:00:00
5
1008

Current Day: 2018-01-10 00:00:00
5
1008

Current Day: 2018-01-11 00:00:00
5
1008

Curren

NET MONEY FROM LIQUIDATION: 126.0

Current Day: 2018-08-13 00:00:00
5
1008

Current Day: 2018-08-14 00:00:00
5
1008

Current Day: 2018-08-15 00:00:00
5
1008

Current Day: 2018-08-16 00:00:00
5
1008

Current Day: 2018-08-17 00:00:00
5
1008

Current Day: 2018-08-20 00:00:00
5
1008

Current Day: 2018-08-21 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 20.0

Current Day: 2018-08-22 00:00:00
5
1008

Current Day: 2018-08-23 00:00:00
5
1008

Current Day: 2018-08-24 00:00:00
5
1008

Current Day: 2018-08-27 00:00:00
5
1008

Current Day: 2018-08-28 00:00:00
5
1008

Current Day: 2018-08-29 00:00:00
5
1008

Current Day: 2018-08-30 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: -526.0

Current Day: 2018-08-31 00:00:00
5
1008

Current Day: 2018-09-03 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 291.375

Current Day: 2018-09-04 00:00:00
5
1008

Current Day: 2018-09-05 00:00:00
5
1008

Current Day: 2018-09-06 00:00:00
5
1008

Current Day: 2018-09-07 00:00:00
5
1008

Current Day: 2018-09-10 00:00:00
5
1008




Current Day: 2019-04-11 00:00:00
5
1008

Current Day: 2019-04-12 00:00:00
5
1008

Current Day: 2019-04-15 00:00:00
5
1008

Current Day: 2019-04-16 00:00:00
5
1008

Current Day: 2019-04-17 00:00:00
5
1008

Current Day: 2019-04-18 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: -199.5

Current Day: 2019-04-19 00:00:00
5
1008

Current Day: 2019-04-22 00:00:00
5
1008

Current Day: 2019-04-23 00:00:00
5
1008

Current Day: 2019-04-24 00:00:00
5
1008

Current Day: 2019-04-25 00:00:00
5
1008

Current Day: 2019-04-26 00:00:00
5
1008

Current Day: 2019-04-29 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: -182.25

Current Day: 2019-04-30 00:00:00
5
1008

Current Day: 2019-05-01 00:00:00
5
1008

Current Day: 2019-05-02 00:00:00
5
1008

Current Day: 2019-05-03 00:00:00
5
1008

Current Day: 2019-05-06 00:00:00
5
1008

Current Day: 2019-05-07 00:00:00
5
1008

Current Day: 2019-05-08 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: -118.5

Current Day: 2019-05-09 00:00:00
5
1008

Current Day: 2019-05-10 00:00:00


Current Day: 2019-12-04 00:00:00
5
1008

Current Day: 2019-12-05 00:00:00
5
1008

Current Day: 2019-12-06 00:00:00
5
1008

Current Day: 2019-12-09 00:00:00
5
1008

Current Day: 2019-12-10 00:00:00
5
1008

Current Day: 2019-12-11 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: -408.25

Current Day: 2019-12-12 00:00:00
5
1008

Current Day: 2019-12-13 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 552.5

Current Day: 2019-12-16 00:00:00
5
1008

Current Day: 2019-12-17 00:00:00
5
1008

Current Day: 2019-12-18 00:00:00
5
1008

Current Day: 2019-12-19 00:00:00
5
1008

Current Day: 2019-12-20 00:00:00
5
1008

Current Day: 2019-12-23 00:00:00
5
1008

Current Day: 2019-12-24 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: -81.75

Current Day: 2019-12-25 00:00:00
5
1008

Current Day: 2019-12-26 00:00:00
5
1008

Current Day: 2019-12-27 00:00:00
5
1008

Current Day: 2019-12-30 00:00:00
5
1008

Current Day: 2019-12-31 00:00:00
5
1008

Current Day: 2020-01-01 00:00:00
5
1008

Current Day: 2020-01-02 00:00:00



Current Day: 2020-08-03 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 170.75

Current Day: 2020-08-04 00:00:00
5
1008

Current Day: 2020-08-05 00:00:00
5
1008

Current Day: 2020-08-06 00:00:00
5
1008

Current Day: 2020-08-07 00:00:00
5
1008

Current Day: 2020-08-10 00:00:00
5
1008

Current Day: 2020-08-11 00:00:00
5
1008

Current Day: 2020-08-12 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 307.25

Current Day: 2020-08-13 00:00:00
5
1008

Current Day: 2020-08-14 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 14.5

Current Day: 2020-08-17 00:00:00
5
1008

Current Day: 2020-08-18 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: -425.0

Current Day: 2020-08-19 00:00:00
5
1008

Current Day: 2020-08-20 00:00:00
5
1008

Current Day: 2020-08-21 00:00:00
5
1008

Current Day: 2020-08-24 00:00:00
5
1008

Current Day: 2020-08-25 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: -522.0

Current Day: 2020-08-26 00:00:00
5
1008

Current Day: 2020-08-27 00:00:00
5
1008

Current Day: 2020-08-28 00:00:00
5
1008

Curren


Current Day: 2021-03-29 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: -227.25

Current Day: 2021-03-30 00:00:00
5
1008

Current Day: 2021-03-31 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 64.0

Current Day: 2021-04-01 00:00:00
5
1008

Current Day: 2021-04-02 00:00:00
5
1008

Current Day: 2021-04-05 00:00:00
5
1008

Current Day: 2021-04-06 00:00:00
5
1008

Current Day: 2021-04-07 00:00:00
5
1008

Current Day: 2021-04-08 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: -302.75

Current Day: 2021-04-09 00:00:00
5
1008

Current Day: 2021-04-12 00:00:00
5
1008

Current Day: 2021-04-13 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 562.25

Current Day: 2021-04-14 00:00:00
5
1008

Current Day: 2021-04-15 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 600.5

Current Day: 2021-04-16 00:00:00
5
1008

Current Day: 2021-04-19 00:00:00
5
1008

Current Day: 2021-04-20 00:00:00
5
1008

Current Day: 2021-04-21 00:00:00
5
1008

Current Day: 2021-04-22 00:00:00
5
1008

Current Day: 2021-04-23 00:00:00
5
1008
NET MO


Current Day: 2021-11-09 00:00:00
5
1008

Current Day: 2021-11-10 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 1230.25

Current Day: 2021-11-11 00:00:00
5
1008

Current Day: 2021-11-12 00:00:00
5
1008

Current Day: 2021-11-15 00:00:00
5
1008

Current Day: 2021-11-16 00:00:00
5
1008

Current Day: 2021-11-17 00:00:00
5
1008

Current Day: 2021-11-18 00:00:00
5
1008

Current Day: 2021-11-19 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: 101.25

Current Day: 2021-11-22 00:00:00
5
1008

Current Day: 2021-11-23 00:00:00
5
1008

Current Day: 2021-11-24 00:00:00
5
1008

Current Day: 2021-11-25 00:00:00
5
1008

Current Day: 2021-11-26 00:00:00
5
1008

Current Day: 2021-11-29 00:00:00
5
1008

Current Day: 2021-11-30 00:00:00
5
1008
NET MONEY FROM LIQUIDATION: -205.25

Current Day: 2021-12-01 00:00:00
5
1008

Current Day: 2021-12-02 00:00:00
5
1008

Current Day: 2021-12-03 00:00:00
5
1008

Current Day: 2021-12-06 00:00:00
5
1008

Current Day: 2021-12-07 00:00:00
5
1008

Current Day: 2021-12-08 00:00:0

In [42]:
create_strat_table(benchmark_test_strategies)

\begin{tabular}{lrrrrrrr}
\hline
 Strat   &   Final capital &    mean &     Std &   sharpe &     dd &   Coefficient &   p-value \\
\hline
 5-1008  &          104693 & 2e-05   & 0.00042 &     0.76 & -0.011 &         0.038 &     0.073 \\
 15-1008 &          105033 & 2.2e-05 & 0.00041 &     0.84 & -0.012 &         0.037 &     0.079 \\
 3-1008  &          105763 & 2.5e-05 & 0.00049 &     0.8  & -0.013 &         0.039 &     0.066 \\
\hline
\end{tabular}


In [43]:
create_strat_table(test_strategies)

\begin{tabular}{lrrrrrrr}
\hline
 Strat   &   Final capital &    mean &     Std &   sharpe &     dd &   Coefficient &   p-value \\
\hline
 5-1008  &          104585 & 2e-05   & 0.00064 &     0.49 & -0.018 &         0.038 &     0.067 \\
 15-1008 &          106157 & 2.6e-05 & 0.00063 &     0.66 & -0.015 &         0.038 &     0.068 \\
 3-1008  &          106357 & 2.7e-05 & 0.00089 &     0.49 & -0.022 &         0.036 &     0.082 \\
\hline
\end{tabular}


In [44]:
create_strat_table(benchmark_test_strategies_exp)

\begin{tabular}{rrrrrrrr}
\hline
   Strat &   Final capital &    mean &     Std &   sharpe &     dd &   Coefficient &   p-value \\
\hline
       5 &          102816 & 1.2e-05 & 0.00038 &     0.51 & -0.019 &         0.033 &      0.11 \\
\hline
\end{tabular}


In [45]:
create_strat_table(test_strategies_exp)

\begin{tabular}{rrrrrrrr}
\hline
   Strat &   Final capital &    mean &     Std &   sharpe &    dd &   Coefficient &   p-value \\
\hline
       5 &          105104 & 2.2e-05 & 0.00054 &     0.64 & -0.01 &         0.037 &     0.077 \\
\hline
\end{tabular}


## Monitor Strategy 

1. History of profit
2. Correct & Incorrect Prediction 
3. When we sell, why are we selling?
    1. Holding period expired? 
    2. Regime switched? 

In [ ]:
fig, ax = plt.subplots(3, 1)
ax[0].plot(df['level'])
ax[1].plot(np.array(strategy.portfolio.profit_hist))
ax[2].plot(np.array(strategy.portfolio.profit_hist).cumsum())

In [ ]:
fig, ax = plt.subplots(2, 1)
ax[0].plot(strategies[3].df['level'])
for hp in strategies:
    st = strategies[hp]
    ax[1].plot(np.concatenate((np.zeros(400), st.portfolio.profit_hist)).cumsum(), label=str(hp))
fig.legend()


In [ ]:
fig, ax = plt.subplots(2, 1)
ax[0].plot(strategies[3].df['level'])
for hp in benchmark_strategies:
    st = benchmark_strategies[hp]
    ax[1].plot(np.concatenate((np.zeros(400), st.portfolio.profit_hist)).cumsum(), label=str(hp))
fig.legend()

In [ ]:
level = df.iloc[:, :10].mean(axis=1).dropna()
volatility = level.rolling(10, min_periods=10).apply(stdev)
strat_df = df.iloc[:, :10]
strat_df['level'] = level
strat_df['volatility'] = volatility


In [104]:
from scipy.stats import spearmanr, pearsonr

In [73]:
from scipy.stats import spearmanr, pearsonr
level_table = []
return_table = []
# Level and Volatility
level_sp = spearmanr(level,  df['volatility'].fillna(df['volatility'].mean())[1:])
level_pr = pearsonr(level,  df['volatility'].fillna(df['volatility'].mean())[1:])

level_table.append([float('%.2g' % level_sp[0]), float('%.2g' % level_sp[1])])
level_table.append([float('%.2g' % level_pr[0]), float('%.2g' % level_pr[1])])

# Log Return and Volatility
returns_sp = spearmanr(level.pct_change().bfill(), df['volatility'].fillna(df['volatility'].mean()).diff().bfill()[1:])
returns_pr = pearsonr(level.pct_change().bfill(),  df['volatility'].fillna(df['volatility'].mean()).diff().bfill()[1:])

return_table.append([float('%.2g' % returns_sp[0]), float('%.2g' % returns_sp[1])])
return_table.append([float('%.2g' % returns_pr[0]), float('%.2g' % returns_pr[1])])



print(tabulate(level_table, headers=["Coefficient", "p-value"], tablefmt='latex_raw'))
print(tabulate(return_table, headers=["Coefficient", "p-value"], tablefmt='latex_raw'))

\begin{tabular}{rr}
\hline
   Coefficient &   p-value \\
\hline
          0.53 &  1.7e-229 \\
          0.54 &  7.3e-237 \\
\hline
\end{tabular}
\begin{tabular}{rr}
\hline
   Coefficient &   p-value \\
\hline
      -0.00065 &    0.97   \\
      -0.055   &    0.0021 \\
\hline
\end{tabular}


In [ ]:
import os
os.environ["PATH"] += os.pathsep + '/usr/local/texlive/2022/bin/universal-darwin'

In [128]:
# ACF PLOTS
%matplotlib qt
import statsmodels.api as sm
fig, (ax1, ax2) = plt.subplots(2,1)
fig.suptitle("ACF plots")
fig.set_size_inches(w=6.10356, h=5)

# LEVEL
sm.graphics.tsa.plot_acf(level, lags=40, ax=ax1)
ax1.set_title("Level")
ax1.set_xlabel("Lag")

# LOG RETURNS
sm.graphics.tsa.plot_acf(level.pct_change().bfill(), lags=40, ax=ax2)
ax2.set_title("Log returns")
ax2.set_xlabel("Lag")

plt.tight_layout()
if savefig: plt.savefig('ACF.pgf')


In [ ]:
# Possibly won't be including this! 

print(sm.stats.acorr_ljungbox(level, lags=[40], return_df=True))
print(sm.stats.acorr_ljungbox(volatility.fillna(volatility.mean()), lags=[40], return_df=True))
print(sm.stats.acorr_ljungbox(level.pct_change().bfill(), lags=[40], return_df=True))
print(sm.stats.acorr_ljungbox(volatility.diff().fillna(volatility.diff().mean()), lags=[40], return_df=True))

# Pragmatic Number of Hidden State Selection

In [119]:
from tabulate import tabulate

In [34]:
obs1 = final_train_df['level'].pct_change().bfill()
obs2 = final_train_df['volatility'].diff().fillna(df['volatility'].diff().mean())
#X = [[x[0], x[1]] for x in zip(obs1, obs2)]
X = obs1

In [35]:
best_hmm_bic, bic, bic_history, models_bic = bic_hmmlearn(X, 2, 5)
best_hmm_aic, aic, aic_history, models_aic = aic_hmmlearn(X, 2, 5)

In [36]:
def get_state_df(df, hidden_states, start, end, obs):
    '''
    Want to take a df and an array of the hidden states derived from that df,
    and then use this to gice us a new dataframe where each column is the entries for the hs.
    '''
    diff = len(df) - len(hidden_states)
    df = df[diff:].copy()
    df['hidden_states'] = hidden_states
    result = pd.DataFrame()
    result = result.reindex(pd.date_range(start=start, end=end, freq='B'))
    result = result.set_index(result.index.rename("Date"))
    for hs in np.unique(hidden_states):
        state_data = df[df['hidden_states'] == hs]
        result = result.merge(state_data[obs], how='left', on='Date')
    result.columns = np.unique(hidden_states)
    return result



In [200]:
# Get Parameters
for model in models_bic:
    hs = model.decode(np.array(X).reshape(-1, 1))[1]
    hs_df = get_state_df(final_train_df, hs, final_train_df.index[0], final_train_df.index[-1], 'obs1')

    table = []
    for i, col in enumerate(hs_df.columns):
        state_data = hs_df[col]
        state = col
        observation_count = state_data.dropna().count()
        mean = float('%.2g' % state_data.dropna().mean())
        std = float('%.2g' % state_data.dropna().std())
        persistence = float('%.2g' % (100*model.transmat_[i][i]))
        
        table.append([state, observation_count, mean, std, persistence])
    
    headers = ["State", "Number of observations", "Mean", "Std", "Persistence (%)"]
    print(tabulate(table, headers, tablefmt='latex', numalign='decimal'))

\begin{tabular}{rrrrr}
\hline
   State &   Number of observations &    Mean &    Std &   Persistence (\%) \\
\hline
       0 &                      300 &  0.011  & 0.025  &                48 \\
       1 &                     1602 & -0.0021 & 0.0085 &                53 \\
\hline
\end{tabular}
\begin{tabular}{rrrrr}
\hline
   State &   Number of observations &     Mean &    Std &   Persistence (\%) \\
\hline
       0 &                     1582 & -0.00022 & 0.0081 &                55 \\
       1 &                      164 &  0.027   & 0.011  &                30 \\
       2 &                      156 & -0.025   & 0.0095 &                29 \\
\hline
\end{tabular}
\begin{tabular}{rrrrr}
\hline
   State &   Number of observations &    Mean &    Std &   Persistence (\%) \\
\hline
       0 &                     1377 & -0.0023 & 0.0068 &                39 \\
       1 &                      251 &  0.013  & 0.0068 &                35 \\
       2 &                      127 &  0.024  & 0.02   &    

/var/folders/bn/nf5j5v796jjb6bncp9wnk5l80000gn/T/ipykernel_997/2885157279.py:16: FutureWarning: Passing 'suffixes' which cause duplicate columns {'obs1_x'} in the result is deprecated and will raise a MergeError in a future version.
  result = result.merge(state_data[obs], how='left', on='Date')


In [43]:
# Time Series Plot

fig, ax = plt.subplots(3, 1)
fig.set_size_inches(w=6.10356, h=5)

for i, model in enumerate(models_bic):
    hs = model.decode(np.array(X).reshape(-1, 1))[1]
    hs_df = get_state_df(final_train_df, hs, final_train_df.index[0], final_train_df.index[-1], 'obs1')
    for col in hs_df.columns:
        # Want a way to plot on the same axis so we can see how the distributions are broken up.  
        state_data = hs_df[col]
        ax[i].plot(state_data, label="Hidden State: {}".format(col))
        ax[i].set_xlabel("Date")
        ax[i].set_ylabel("Log-returns")
        fig.suptitle("Viterbi-coded observation sequence")

if savefig: plt.savefig("ts.pgf".format(model.n_components))
plt.plot()

/var/folders/bn/nf5j5v796jjb6bncp9wnk5l80000gn/T/ipykernel_6431/1829372222.py:14: FutureWarning: Passing 'suffixes' which cause duplicate columns {'obs1_x'} in the result is deprecated and will raise a MergeError in a future version.
  result = result.merge(state_data[obs], how='left', on='Date')


[]

In [145]:
%matplotlib qt
import seaborn as sns
# Indvidual distribution plot for observation

fig, ax = plt.subplots(3, 1)
fig.set_size_inches(w=6.10356, h=5)

for i,model in enumerate(models_bic):
    hs = model.decode(np.array(X).reshape(-1, 1))[1]
    dummy_df = final_train_df.copy()
    dummy_df['hidden_states'] = hs
    dummy_df['obs1'] = dummy_df['obs1']
    
    sns.kdeplot(data=dummy_df, x='obs1', hue='hidden_states', ax=ax[i], shade=True)
    ax[i].set_ylim(0, 10)
    plt.suptitle("Distributions of log-returns in states")
    plt.xlabel("Log-returns")
    plt.plot()
    
if savefig: plt.savefig("states.pgf")

In [142]:
# Q-Q plots
import scipy.stats as stats

for model in models_bic[:2]:
    hs = model.decode(np.array(X).reshape(-1, 1))[1]
    hs_df = get_state_df(final_train_df, hs, final_train_df.index[0], final_train_df.index[-1], 'obs1')
    fig, ax = plt.subplots(len(hs_df.columns), 1)
    fig.set_size_inches(w=6.10356, h=5)

    for i, col in enumerate(hs_df.columns):
        # Want a way to plot on the same axis so we can see how the distributions are broken up.  
        state_data = hs_df[col]
        stats.probplot(state_data.dropna(), dist="norm", plot=ax[i])
        ax[i].set_title("State: {}".format(col))
        plt.tight_layout()
               
    if savefig: plt.savefig("qq_{}.pgf".format(model.n_components))
    plt.show() 
    
    
# hs = models_bic[2].decode(np.array(X).reshape(-1, 1))[1]
# hs_df = get_state_df(final_train_df, hs, final_train_df.index[0], final_train_df.index[-1], 'obs1')
# fig, ax = plt.subplots(2, 2)
# fig.set_size_inches(w=6.10356, h=5)

# count=0
# for i, col in enumerate(hs_df.columns):
#     state_data = hs_df[col]
#     if count > 1:
#         stats.probplot(state_data.dropna(), dist="norm", plot=ax[1][i%2])
#         ax[1][i%2].set_title("State: {}".format(col))
#     else:
#         stats.probplot(state_data.dropna(), dist="norm", plot=ax[0][i%2])
#         ax[1][i%2].set_title("State: {}".format(col))
#     count += 1
#     plt.tight_layout()

# if savefig: plt.savefig("qq_{}.pgf".format(models_bic[2].n_components))
# plt.show() 


/var/folders/bn/nf5j5v796jjb6bncp9wnk5l80000gn/T/ipykernel_1000/3109168040.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['hidden_states'] = hidden_states
/var/folders/bn/nf5j5v796jjb6bncp9wnk5l80000gn/T/ipykernel_1000/3109168040.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['hidden_states'] = hidden_states


In [132]:
# Plotting AIC and BIC
fig,ax = plt.subplots()
fig.set_size_inches(w=6.10356, h=5)
plt.xlabel("Number of states")
plt.ylabel("IC")
ax.plot([2,3,4], aic, label='AIC')
ax.plot([2,3,4], bic, label='BIC')
plt.title("AIC vs BIC")
plt.legend()
if savefig: plt.savefig("aicbic_{}.pgf")
plt.show()

In [ ]:
def create_strat_table(strategies):
    print("Rolling Window \n")
    table = []
    for st in strategies:
        strat = [strategies[st]]
        invested = np.array(strat.portfolio.invested).sum()
        profit = strat.portfolio.profit
        std = np.array(strat.portfolio.profit_hist).std()
        profit_percentage = (profit+invested)*100/invested
        profit_adj = ((profit+invested)*100)/(invested*std)

        table.append([st, invested, profit, std, profit_percentage, profit_adj])
    
    headers = ["Strat", "Money Invested", "Profit", "Std", "Profit %", "Profit adjusted"]
    return tabulate(table, headers)

In [ ]:
print("Rolling Window \n")

for st in test_strategies:
    invested = np.array(test_strategies[st].portfolio.invested).sum()
    profit = test_strategies[st].portfolio.profit
    std = np.array(test_strategies[st].portfolio.profit_hist).std()
    print("Strategy: {}\n".format(st))
    print("Money invested: {}".format(invested))
    print("Profit: {}".format(profit))
    print("Profit: {}%".format((profit+invested)*100/invested))
    print("Standard Deviation: {}".format(std))
    print("Risk-adjusted Profit: {}\n".format(((profit+invested)*100)/(invested*std)))

In [ ]:
print("Expanding Window \n")

for st in expanding_strats:
    invested = np.array(expanding_strats[st].portfolio.invested).sum()
    profit = expanding_strats[st].portfolio.profit
    std = np.array(expanding_strats[st].portfolio.profit_hist).std()
    print("Strategy: {}\n".format(st))
    print("Money invested: {}".format(invested))
    print("Profit: {}".format(profit))
    print("Profit: {}%".format((profit+invested)*100/invested))
    print("Standard Deviation: {}".format(std))
    print("Risk-adjusted Profit: {}\n".format(((profit+invested)*100)/(invested*std)))

In [106]:
from sklearn.decomposition import PCA
from sklearn.preprocessing import StandardScaler
import numpy as np
        
        #print(kmo(X.dropna().corr()))
idx = final_train_df.index        
pca = PCA(10)
X = final_train_df.iloc[:, :10].dropna()
X_scaled = StandardScaler().fit_transform(X)
pca.fit(X_scaled)
scores = pca.transform(X_scaled)
loadings = pca.components_
reconstructed_data = pd.DataFrame(np.dot(scores, loadings))
eig_vals = pca.explained_variance_

In [95]:
%matplotlib qt
pd.DataFrame(loadings).plot.scatter(x='1', y='')

TypeError: scatter() missing 2 required positional arguments: 'x' and 'y'

In [101]:
pd.DataFrame(scores).plot.scatter(x=0, y=1)

<AxesSubplot:xlabel='0', ylabel='1'>

In [112]:
plt.xlabel("Number of principle components")
plt.ylabel("Explained Variance")
plt.title("Explained variance for entire training dataset")
plt.plot(eig_vals.cumsum() * 10)
plt.savefig('elbowplot.pgf')

In [107]:
eig_vals

array([9.77072456e+00, 8.27215793e-02, 6.19722884e-02, 4.40784738e-02,
       3.01758374e-02, 6.42772029e-03, 4.26605011e-03, 2.84871508e-03,
       1.42961658e-03, 6.18318835e-04])

In [114]:
final_train_df

0        1       2        3        4        5        6  \
Date                                                                      
2010-01-01     NaN      NaN     NaN      NaN      NaN      NaN      NaN   
2010-01-04  418.50  428.750  437.00  441.000  445.250  454.000  460.250   
2010-01-05  418.75  429.000  437.50  441.750  445.250  456.125  462.250   
2010-01-06  421.75  432.000  440.75  444.750  448.750  458.250  464.250   
2010-01-07  417.50  428.000  436.75  440.000  443.500  453.000  459.000   
...            ...      ...     ...      ...      ...      ...      ...   
2017-04-11  366.50  373.750  380.75  390.500  399.250  405.000  410.000   
2017-04-12  369.00  376.000  382.75  392.500  401.000  406.750  411.500   
2017-04-13  371.00  378.000  384.50  394.500  403.500  409.250  413.750   
2017-04-14  368.75  375.625  382.25  392.375  401.625  407.250  411.625   
2017-04-17  366.50  373.250  380.00  390.250  399.750  405.250  409.500   

                  7        8       9    level  volatility      obs1      obs2  
Date                                                                           
2010-01-01      NaN      NaN     NaN      NaN         NaN  0.003029 -0.002247  
2010-01-04  465.250  456.250  451.25  445.750         NaN  0.003029 -0.002247  
2010-01-05  467.375  458.500  454.50  447.100         NaN  0.003029 -0.002247  
2010-01-06  469.500  460.750  457.75  449.850         NaN  0.006151 -0.002247  
2010-01-07  464.250  455.500  452.50  445.000         NaN -0.010781 -0.002247  
...             ...      ...     ...      ...         ...       ...       ...  
2017-04-11  404.250  406.250  413.00  394.925    3.715098 -0.000949 -0.111186  
2017-04-12  405.750  407.000  414.00  396.625    3.586766  0.004305 -0.128332  
2017-04-13  407.250  407.750  414.50  398.400    2.974719  0.004475 -0.612047  
2017-04-14  404.875  405.625  412.50  396.250    3.037919 -0.005397  0.063200  
2017-04-17  402.500  403.500  410.50  394.100    3.006655 -0.005426 -0.031264  

[1902 rows x 14 columns]

In [118]:

final_train_df.iloc[:, :10].plot()

<AxesSubplot:xlabel='Date'>

In [32]:
final_test_df_fixed

0       1       2       3       4       5       6       7  \
Date                                                                         
2013-06-06  663.25  578.00  548.25  558.75  566.00  572.75  563.50  560.50   
2013-06-07  666.25  591.50  558.50  568.75  576.00  582.25  570.75  565.50   
2013-06-10  650.00  577.25  546.00  556.50  563.75  570.50  561.25  558.75   
2013-06-11  659.50  583.50  550.75  561.50  568.75  575.50  565.50  561.50   
2013-06-12  650.75  575.00  537.50  548.25  555.25  562.25  554.50  551.25   
...            ...     ...     ...     ...     ...     ...     ...     ...   
2022-02-21  654.25  652.75  647.00  608.75  597.75  604.75  608.25  609.75   
2022-02-22  674.75  672.50  665.25  621.00  605.75  612.75  616.25  617.75   
2022-02-23  683.75  681.25  674.50  628.75  611.25  618.00  621.50  622.75   
2022-02-24  695.00  690.25  678.50  620.75  604.75  611.00  614.25  615.50   
2022-02-25  659.50  655.75  644.00  594.25  579.75  586.75  590.00  591.50   

                 8       9    level  volatility      obs1      obs2  
Date                                                                 
2013-06-06  566.50  570.00  574.750    7.618691  0.008599 -1.082865  
2013-06-07  572.00  575.50  582.700    6.311999  0.013832 -1.306692  
2013-06-10  565.25  568.75  571.800    6.239358 -0.018706 -0.072642  
2013-06-11  568.00  571.50  576.600    6.273489  0.008395  0.034132  
2013-06-12  558.00  561.75  565.450    6.938590 -0.019337  0.665101  
...            ...     ...      ...         ...       ...       ...  
2022-02-21  569.00  560.25  611.250    5.768403       NaN       NaN  
2022-02-22  576.75  567.75  623.050    6.672539       NaN       NaN  
2022-02-23  579.25  570.00  629.100    8.999049       NaN       NaN  
2022-02-24  571.75  563.50  626.525    9.124190       NaN       NaN  
2022-02-25  551.00  543.00  599.550   10.086837       NaN       NaN  

[2277 rows x 14 columns]